### Misc functions


In [3]:
# Misc. functions for plotting
def plot_traj(sol, number_of_variables, hide_legends = False):
    import matplotlib.pyplot as plt
    plt.grid(True)
    plt.title('Spin variables')
    for i, spin_var in enumerate(sol.y[0:number_of_variables]):
        x = sol.t
        y = spin_var
        plt.plot(x, y, label='s'+str(i+1))
    if not hide_legends:
        plt.legend()
    plt.show()

def plot_traj_js(solver, time_distance_flag = False):
    import plotly.graph_objects as go
    fig = go.Figure()
    N = solver.problem.number_of_variables
    if time_distance_flag:
        my_x = solver.get_sol_length()
    else:
        my_x = solver.sol.t

    for idx, traj in enumerate(solver.sol.y):
        if idx <N:
            fig.add_trace(go.Scatter(x=my_x, y=traj, name=str(idx+1), mode='lines'))
    
    if time_distance_flag:
        fig.update_xaxes(title_text="Trajectory length", type="linear")
    else:
        fig.update_xaxes(title_text="Continuous time", type="linear")
    
    fig.update_yaxes(title_text="Spin variables")

    fig.show()

def plot_aux_js(solver, time_distance_flag = False, aux_prune = None, LOG_YAXIS_FLAG = True):
    import plotly.graph_objects as go
    fig = go.Figure()
    N = solver.problem.number_of_variables
    M = solver.problem.number_of_clauses
    if time_distance_flag:
        my_x = solver.get_sol_length()
    else:
        my_x = solver.sol.t

    for idx, traj in enumerate(solver.sol.y):
        if not aux_prune:
            if idx >= N:
                if traj[-1] > 0.0:
                    fig.add_trace(go.Scatter(x=my_x, y=traj, name=str(idx+1-N), mode='lines'))
        else:
            if idx in aux_prune:
                fig.add_trace(go.Scatter(x=my_x, y=traj, name=str(idx+1-N), mode='lines'))
    
    if time_distance_flag:
        fig.update_xaxes(title_text="Trajectory length", type="linear")
    else:
        fig.update_xaxes(title_text="Continuous time", type="linear")
    
    if LOG_YAXIS_FLAG:
        fig.update_yaxes(title_text="Auxiliary variables", type="log")
    else:
        fig.update_yaxes(title_text="Auxiliary variables", type="linear")

    fig.show()

def plot_C_of_t(*args):
    import plotly.graph_objects as go
    fig = go.Figure()
    for idx, traj_pairs in enumerate(args):
        t, traj = traj_pairs
        fig.add_trace(go.Scatter(x=t, y=traj, mode='lines+markers'))
    fig.update_xaxes(title_text="Time", type="linear")
    fig.show()

def plot_trej_length_afo_time(solver):
    import matplotlib.pyplot as plt
    plt.grid(True)
    plt.plot(solver.sol.t, solver.get_sol_length())
    plt.plot(solver.sol.t, solver.sol.t)
    plt.xlabel("Analog time")
    plt.ylabel("Trajectory length")

def generate_sym_heatmap_from_matrix(solver):
    import numpy as np

    N = solver.problem.number_of_variables
    M = solver.problem.number_of_clauses

    # Create an empty MxM matrix
    matrix = np.ones((M, M))

    # Iterate all the variables
    if solver.problem.G is None:
        for idx, traj in enumerate(solver.sol.y):
            if idx >= N:
                # The first N points are not part of the matrix
                i = idx-N
                # The indices of the matrix
                m = int(i/M)
                n = i % M
                matrix[m][n] = traj[-1] # Saving only the last matrix from the list into the variable 'matrix'
    else:
        edges =  list(solver.problem.G.edges)
        for idx, traj in enumerate(solver.sol.y):
            if idx >= N:
                (m, n) = edges[idx - N]
                matrix[m][n] = traj[-1] # Saving only the last matrix from the list into the variable 'matrix'


    plot_matrix_js(matrix)

def plot_matrix_js(matrix, title=None):
    import plotly.express as px
    
    # Define custom color scale
    # Define custom color scale
    colorscale = [[0, 'darkblue'], [0.5, 'white'], [1, 'darkred']]
    
    # Create the heatmap plot using PlotlyJS with custom color scale
    fig = px.imshow(matrix, text_auto=True, aspect="equal", color_continuous_scale=colorscale, color_continuous_midpoint=0.0)
    
    # Update layout to include title
    if title:
        fig.update_layout(title=title)
    
    fig.show()

def generate_sym_heatmap_from_flatvec(solver):
    import plotly.express as px
    import numpy as np

    N = solver.problem.number_of_variables
    M = solver.problem.number_of_clauses

    b_mn = np.zeros(int(M*(M+1)/2))
    for idx, traj in enumerate(solver.sol.y):
        if idx > N:
            b_mn[idx-N-1] = traj[-1]
    
    # Create an empty NxN matrix
    matrix = np.zeros((M, M))

    # Fill the upper triangle of the matrix using the input vector
    index = 0
    for m in range(M):
        for n in range(M):
            if n >= m:
                matrix[m][n] = b_mn[index]
                index += 1

    # Create the heatmap plot using PlotlyJS
    fig = px.imshow(matrix, text_auto=True, aspect="auto")
    fig.show()

def memory_distribution_from_matrix(solver, num_buckets=50):
    import plotly.graph_objects as go
    import numpy as np

    N = solver.problem.number_of_variables
    M = solver.problem.number_of_clauses

    # Create an empty NxN matrix
    matrix = np.zeros((M, M))

    for idx, traj in enumerate(solver.sol.y):
        if idx >= N:
            i = idx-N
            m = int(i/M)
            n = i % M
            matrix[m][n] = traj[-1]

    vector_data = np.array(matrix).flatten()

    vector_data = np.array([elem for elem in vector_data if elem > 0.01])

    # Create the histogram trace
    trace = go.Histogram(x=vector_data, nbinsx=num_buckets)

    # Create the layout
    layout = go.Layout(
        title='Histogram',
        xaxis=dict(title='Values'),
        yaxis=dict(title='Count'),
    )

    # Create the figure and add the trace
    fig = go.Figure(data=[trace], layout=layout)

    # Display the figure
    fig.show()

def plot_sumk_js(solver, time_distance_flag = False):
    import plotly.graph_objects as go
    import numpy as np

    fig = go.Figure()
    N = solver.problem.number_of_variables
    M = solver.problem.number_of_clauses
    if time_distance_flag:
        my_x = solver.get_sol_length()
    else:
        my_x = solver.sol.t

    s_t = np.zeros((N, len(my_x)))
    for idx, traj in enumerate(solver.sol.y):
        if idx <N:
            for t, elem in enumerate(traj):
                s_t[idx][t] = elem
    
    k_t = np.zeros((len(my_x), M))
    for t, s in enumerate(s_t):
        k_t[t] = sum( solver.problem.K(m, s) for m in range(M) )
    
    fig.add_trace(go.Scatter(x=my_x, y=k_t, name='my name', mode='lines'))
    
    if time_distance_flag:
        fig.update_xaxes(title_text="Trajectory length", type="linear")
    else:
        fig.update_xaxes(title_text="Continuous time", type="linear")
    
    fig.update_yaxes(title_text="Potential value")

    fig.show()

def generate_sym_heatmap_video_from_matrices(solver, filename='heatmap_video.mp4', ABSOLUTE_COLOR_FLAG = False):
    import numpy as np
    import matplotlib.pyplot as plt
    from matplotlib.animation import FuncAnimation
    
    def extract_matrices_from_solver(solver):
        N = solver.problem.number_of_variables
        M = solver.problem.number_of_clauses
        matrices = []
        vmin = None
        vmax = None

        for m_index in range(len(solver.sol.t)):
            # Create an empty MxM matrix
            matrix = np.ones((M, M))

            # Iterate all the variables
            if solver.problem.G is None:
                for idx, traj in enumerate(solver.sol.y):
                    if idx >= N:
                        # The first N points are not part of the matrix
                        i = idx-N
                        # The indices of the matrix
                        m = int(i/M)
                        n = i % M
                        matrix[m][n] = traj[m_index]
            else:
                edges =  list(solver.problem.G.edges)
                for idx, traj in enumerate(solver.sol.y):
                    if idx >= N:
                        (m, n) = edges[idx - N]
                        matrix[m][n] = traj[m_index]
            
            matrices.append(matrix)
        
        return matrices

    # Define the function to update the plot for each frame
    def update(frame):
        plt.clf()
        plt.imshow(matrices[frame], cmap='viridis', vmin=vmin, vmax=vmax)
        plt.title(f'Analog time {solver.sol.t[frame]}')
    

    matrices = extract_matrices_from_solver(solver)
    if (ABSOLUTE_COLOR_FLAG):
        vmin = np.min([np.min(matrix) for matrix in matrices])
        vmax = np.max([np.max(matrix) for matrix in matrices])

    # Create a figure and axis
    fig, ax = plt.subplots()
    ani = FuncAnimation(fig, update, frames=len(matrices), interval=200)
    
    # Save the animation to a file
    ani.save(filename, writer='ffmpeg')

In [ ]:
# Old misc. functions
def plot_array(myArray):
    import matplotlib.pyplot as plt
    plt.grid(True)
    plt.title('Spin variables')
    plt.plot(myArray, label='s'+str(i+1))
    plt.legend()
    plt.show()

def plot_aux(sol, number_of_variables, hide_legends = False, appl_fnc = lambda x : x):
    import matplotlib.pyplot as plt
    plt.grid(True)
    plt.title('Aux variables')
    for i, spin_var in enumerate(sol.y[number_of_variables:]):
        x = appl_fnc(sol.t)
        y = appl_fnc(spin_var)
        plt.plot(x, y, label='s'+str(i+1))
    if not hide_legends:
        plt.legend()
    plt.show()

def save_plot_traj(sol, number_of_variables, file_name):
    import matplotlib.pyplot as plt
    plt.grid(True)
    plt.title('Spin variables')
    for i, spin_var in enumerate(sol.y[0:number_of_variables]):
        x = sol.t
        y = spin_var
        plt.plot(x, y, label='s'+str(i+1))
    plt.legend()
    plt.savefig(file_name+ '.png', dpi=350)

def plot_error_effect(data_dict, max_time = 1000, number_of_points = 100, hide_legends = False):
    import matplotlib.pyplot as plt
    import numpy as np
    plt.grid(True)
    plt.title('Effect of absolute tolerance')
    plt.xlabel('Analog time')
    plt.ylabel('Ratio of the unfinished init, conds')
    plt.yscale('log')
    times = np.linspace(0.0, max_time, number_of_points)
    for key, vals in data_dict.items():
        ratios = [len([elem for elem in vals if elem > t])/len(vals) for t in times]
        plt.plot(times, ratios, label=str(key))
    if not hide_legends:
        plt.legend()
    plt.show()

def save_error_effect(data_dict, file_name, max_time = 1000, number_of_points = 100, hide_legends = False):
    import matplotlib.pyplot as plt
    import numpy as np
    plt.grid(True)
    plt.title('Effect of absolute tolerance')
    plt.xlabel('Analog time')
    plt.ylabel('Ratio of the unfinished init. ,conds')
    plt.yscale('log')
    times = np.linspace(0.0, max_time, number_of_points)
    for key, vals in data_dict.items():
        ratios = [len([elem for elem in vals if elem > t])/len(vals) for t in times]
        plt.plot(times, ratios, label=str(key))
    if not hide_legends:
        plt.legend()
    plt.savefig(file_name+ '.png', dpi=350)


## General testing

### Problem instance

In [2]:
from pySAT import SAT, CTD, ORTANT, HYPER_SPHERE, Warning_propagator
import numpy as np

so_file_name = 'c_libs/cSat.so'
#so_file_name = None
#myProblem = SAT('SAT_problems/random3SATn15a4.266666666666667.cnf', so_file_name, rhs_type=12, lmbd=0.4)
#myProblem = SAT("SAT_problems\\SATLIB_Benchmark_problems_N50\\uf50-06.cnf", so_file_name, rhs_type=3, lmbd=0.00001)
myProblem = SAT("SAT_problems\\SATLIB_Benchmark_problems_N20\\uf20-01.cnf", so_file_name, rhs_type=12, lmbd=0.00001)
#myProblem = SAT("SAT_problems\\SATLIB_Benchmark_problems_N75\\uf75-09.cnf", so_file_name, rhs_type=3, lmbd=0.00001)
#myProblem = SAT("SAT_problems/random3SATn60a4.9.cnf", so_file_name, rhs_type=3, lmbd=1.1)
#myProblem = SAT("C:\\Projects\\cppSAT\\pySat\\SAT_problems\\benchmark30\\random3SATn30M128_1.cnf", so_file_name, rhs_type=3, lmbd=0.4)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses
#

wp = Warning_propagator(myProblem)
myProblem.set_G(wp.generate_upper_triangular_graph(M))

In [4]:
#init_s = 2*np.random.rand(N) - np.ones(N)
#init_a = 10*np.ones(M)
#init_state = np.concatenate((init_s, init_a))
#init_z = np.zeros(M)
init_s =np.array([-0.95145001, 0.11232692, 0.64426413, -0.79373686,  0.55489709, -0.56603168,
  0.89220419,  0.5998528,   0.40443533, -0.475084,   -0.3823661,  -0.08930298,
  0.635762,    0.29987936, -0.66464255,  0.12724873, -0.67057422, -0.58255904,
 -0.77904007, -0.97668135])

init_s = np.array([-0.999593, -0.160035, 0.291477, 0.849807, 0.703896, 0.385878, -0.553680, 0.300965, 0.323413, -0.395969, 0.942108, 0.009651, 0.210198, 0.797750, -0.219995, 0.544410, -0.100232, -0.599694, 0.937614, 0.475796])


In [136]:
init_s = np.array([0.30731878, -0.27320822,  0.69448816, -0.4512187,  0.21111388, -0.2145188,
 -0.48186634,  0.64581068,  0.37127888, -0.74369048, -0.43390443,  0.01679758,
  0.72723414,  0.52383138,  0.22046739,  0.48625664, -0.98359084,  0.9253299
,  0.19716294, -0.37073519])

In [5]:
solver = CTD(myProblem, initial_s=init_s, random_aux=False)
solver.fast_solve(t_max=55, solver_type='LSODA', exit_type=ORTANT)

In [ ]:
plot_traj_js(solver, False)

In [ ]:
plot_traj_js(solver2, False)

In [114]:
if solver2.problem.check_solution([True if elem > 0 else False for elem in solver.sol.y[:N,-1]]):
    print('yey')

yey


In [ ]:
plot_aux_js(solver, False)

Exception ignored in: <bound method IPythonKernel._clean_thread_parent_frames of <ipykernel.ipkernel.IPythonKernel object at 0x0000015919857A10>>
Traceback (most recent call last):
  File "c:\Projects\cppSAT\pySat\.venv\Lib\site-packages\ipykernel\ipkernel.py", line 785, in _clean_thread_parent_frames
    active_threads = {thread.ident for thread in threading.enumerate()}
                                                 ^^^^^^^^^^^^^^^^^^^^^
  File "c:\Program Files\Python312\Lib\threading.py", line 1533, in enumerate
    def enumerate():
    
KeyboardInterrupt: 


In [16]:
t, s = solver.get_satisfied_C_of_t()
plot_C_of_t((t, [elem/M for elem in s]))

In [4]:
solver.save_solver_to_file('dummy_file.sol', sparsify=1)

In [3]:
solver2 = CTD.load_sol_from_file('dummy_file.sol', myProblem)

In [ ]:
s_t = np.zeros((N, len(solver.sol.y[0])))
s_t[:, :] = solver.sol.y[:N]
time_size = len(s_t[0,:])
k_t = np.zeros(time_size)

for t in range(time_size):
    k_t[t] = sum( [solver.problem.K(m, s_t[:, t]) for m in range(M)])

#k_t = np.zeros((time_size, M))
#
#for t in range(time_size):
#    k_t[t,:] = np.array([solver.problem.K(m, s_t[:, t]) for m in range(M)])



In [ ]:
import plotly.graph_objects as go
import numpy as np

fig = go.Figure()
my_x = solver.sol.t

#for m in range(M):
#    fig.add_trace(go.Scatter(x=my_x, y=k_t[:,m], name='K_'+str(m) , mode='lines'))

fig.add_trace(go.Scatter(x=my_x, y=k_t, name='my name', mode='lines'))
fig.update_xaxes(title_text="Continuous time", type="linear")
fig.update_yaxes(title_text="Potential value")

fig.show()

In [ ]:
plot_trej_length_afo_time(solver)
t, s = solver.get_satisfied_C_of_t()
plot_C_of_t((t, [elem/M for elem in s]))

In [ ]:
myProblem.lmdb = 0.02
init_s = 2*np.random.rand(N) - np.ones(N)
#init_z = np.zeros(M)
#init_s = [-0.31258344,  0.49073212,  0.97036443,  0.11065268, -0.01694477,
#       -0.38889108,  0.47987746,  0.30550421, -0.40930195,  0.92859011,
#       -0.96330518, -0.99402537, -0.04915952, -0.39642377,  0.87447153]
solver = CTD(myProblem, initial_s=init_s, random_aux=False, initial_aux=np.ones(M))
solver.fast_solve(t_max=75, solver_type='RK45', exit_type=ORTANT)

In [ ]:
#plot_traj_js(solver.sol, N)
plot_traj(solver.sol, N, True)
plot_aux(solver.sol, N, True)

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_EIGHT, ORTANT, HYPER_SPHERE
import numpy as np

so_file_name = 'c_libs/cSat.so'
myProblem = SAT('SAT_problems/benchmark4.256/random3SATn40M171.cnf', so_file_name, rhs_type=8, lmbd=300)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses


init_s = 2*np.random.rand(N) - np.ones(N)

solver = CTD(myProblem, initial_s=init_s, random_aux=False, initial_aux=2*np.ones(M))
solver.fast_solve(t_max=50, solver_type='RK45', exit_type=None)

plot_aux(solver.sol, N, True)
plot_traj(solver.sol, N, True)

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_THREE, ORTANT, HYPER_SPHERE
import numpy as np

so_file_name = 'c_libs/cSat.so'
#myProblem = SAT(None, so_file_name, rhs_type=RHS_TYPE_THREE, n = 15)
myProblem = SAT('SAT_problems/benchmark_maxaux/random3SATn19M81S4.cnf', so_file_name, rhs_type=RHS_TYPE_THREE)
#myProblem = SAT('SAT_problems/benchmark_maxaux/random3SATn15M64S3.cnf', so_file_name, rhs_type=RHS_TYPE_THREE)
#myProblem = SAT('SAT_problems/benchmark_maxaux/random3SATn16M69S5.cnf', so_file_name, rhs_type=RHS_TYPE_THREE)
myProblem = SAT('SAT_problems/5SAT/unif-p12-k5-r21.117-v250-c5279-S1173863765273039011.cnf', so_file_name, rhs_type=RHS_TYPE_THREE)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses

#print(myProblem.all_solutions())

In [ ]:
import matplotlib.pyplot as plt

init_s =  2*np.random.rand(N) - np.ones(N)

solver = CTD(myProblem, initial_s=init_s, random_aux=False)
solver.fast_solve(t_max=5, solver_type='RK45', exit_type=None)

print("Max aux:{0}".format(max(solver.sol.y[N:,-1])))
with plt.style.context('ggplot'):#'seaborn-darkgrid'):
    plt.grid(True)
    plt.title('Spin variables')
    for i, spin_var in enumerate(solver.sol.y[0:N]):
        x = solver.sol.t
        y = spin_var
        plt.plot(x, y, label='s'+str(i+1))
        # plt.savefig('exmple_spin'+ '.png', dpi=350)

    # plt.title('Aux variables')
    # for i, spin_var in enumerate(solver.sol.y[N:]):
    #     x = solver.sol.t
    #     y = spin_var
    #     plt.plot(x, y, label='s'+str(i+1))
    #     plt.savefig('exmple_aux'+ '.png', dpi=350)

In [ ]:
set_of_visited_ortants = []
for i in range(len(solver.sol.y[0])):
    ortant_idx = 0
    #str_sol = ""
    for j, elem in enumerate([spin_var_series[i] for spin_var_series in solver.sol.y[0:N]]):
        if elem > 0:
            ortant_idx += 2**j
        #     str_sol += '1'
        # else:
        #     str_sol += '0'
    set_of_visited_ortants.append(ortant_idx)

print(len(set_of_visited_ortants))
print(set_of_visited_ortants)



In [ ]:
no_follow = False
idx_of_to_be_removed = 2
while not no_follow:
    for i, elem in enumerate(set_of_visited_ortants):
        if i == 0:
            idx_of_to_be_removed = -1
        elif i>0 and i < len(set_of_visited_ortants)-1:
            if elem == set_of_visited_ortants[i-1]:
                idx_of_to_be_removed = i
                break
        elif i == len(set_of_visited_ortants)-1:
            print("Exit condition reached")
            no_follow = True
            idx_of_to_be_removed = -1
            break
    
    if idx_of_to_be_removed > 0:
        set_of_visited_ortants.remove(set_of_visited_ortants[idx_of_to_be_removed])

print(len(set_of_visited_ortants))
print(len(set(set_of_visited_ortants)))
#print(set_of_visited_ortants)

In [ ]:
myProblem = SAT('SAT_problems/benchmark4.256/random3SATn90M384.cnf', so_file_name, rhs_type=RHS_TYPE_THREE)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses
init_s =  2*np.random.rand(N) - np.ones(N)

solver = CTD(myProblem, initial_s=init_s, random_aux=False)
solver.fast_solve(t_max=500, solver_type='RK23', exit_type=None)

print("Max aux:{0}".format(max(solver.sol.y[N:,-1])))
with plt.style.context('ggplot'):#'seaborn-darkgrid'):
    plt.grid(True)
    plt.title('Spin variables')
    for i, spin_var in enumerate(solver.sol.y[0:N]):
        x = solver.sol.t
        y = spin_var
        plt.plot(x, y, label='s'+str(i+1))

set_of_visited_ortants = []
for i in range(len(solver.sol.y[0])):
    ortant_idx = 0
    #str_sol = ""
    for j, elem in enumerate([spin_var_series[i] for spin_var_series in solver.sol.y[0:N]]):
        if elem > 0:
            ortant_idx += 2**j
        #     str_sol += '1'
        # else:
        #     str_sol += '0'
    set_of_visited_ortants.append(ortant_idx)

print(len(set_of_visited_ortants))
#print(set_of_visited_ortants)

no_follow = False
idx_of_to_be_removed = 2
while not no_follow:
    for i, elem in enumerate(set_of_visited_ortants):
        if i == 0:
            idx_of_to_be_removed = -1
        elif i>0 and i < len(set_of_visited_ortants)-1:
            if elem == set_of_visited_ortants[i-1]:
                idx_of_to_be_removed = i
                break
        elif i == len(set_of_visited_ortants)-1:
            print("Exit condition reached")
            no_follow = True
            idx_of_to_be_removed = -1
            break
    
    if idx_of_to_be_removed > 0:
        set_of_visited_ortants.remove(set_of_visited_ortants[idx_of_to_be_removed])

print(len(set_of_visited_ortants))
print(len(set(set_of_visited_ortants)))



### Problem generation

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_THREE, ORTANT
import numpy as np

so_file_name = 'c_libs/cSat.so'

for alpha in np.linspace(2, 6, 100):
    myProblem = None
    exit_loop = False
    while(not exit_loop):
        myProblem = SAT(None, so_file_name, n=20, alpha=alpha, rhs_type=RHS_TYPE_THREE)
        print('Number of solutions {0}'.format(len(myProblem.all_solutions())))
        if len(myProblem.all_solutions()) >= 1:
            exit_loop = True
    N, M = myProblem.number_of_variables, myProblem.number_of_clauses
    myProblem.write_problem_to_file('SAT_problems\\benchmark20\\random3SATn'+str(N)+'M'+str(M)+'S'+str(len(myProblem.all_solutions())))


In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_THREE, ORTANT
import numpy as np

so_file_name = 'c_libs/cSat.so'
alpha=4.26

for N in range(10, 22):
    myProblem = None
    exit_loop = False
    while(not exit_loop):
        myProblem = SAT(None, so_file_name, n=N, alpha=alpha, rhs_type=RHS_TYPE_THREE)
        print('Number of solutions {0}'.format(len(myProblem.all_solutions())))
        if len(myProblem.all_solutions()) >= 1 and len(myProblem.all_solutions()) <= 50:
            exit_loop = True
    N, M = myProblem.number_of_variables, myProblem.number_of_clauses
    myProblem.write_problem_to_file('C:\\Projects\\cppSAT\\pySat\\SAT_problems\\scaling_10-25\\random3SAT_N'+str(N)+'M'+str(M)+'S'+str(len(myProblem.all_solutions())))


In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_THREE, ORTANT
import numpy as np

so_file_name = 'c_libs/cSat.so'

myProblem = None
exit_loop = False
target_maxAux = 30#1/(2.5*0.02-0.01)#=25
while(not exit_loop):
    myProblem = SAT(None, so_file_name, n=20, alpha=3.6, rhs_type=RHS_TYPE_THREE)
    print('Number of solutions {0}'.format(len(myProblem.all_solutions())))
    if len(myProblem.all_solutions()) >= 3 and len(myProblem.all_solutions()) <= 6:
        print('Number of clusters {0}'.format(len(myProblem.get_clusters())))
        if len(myProblem.get_clusters()) >= 3:
            ave = average_maxAux(myProblem, 50)
            print("Average max aux {0}".format(ave))
            if ave >= target_maxAux:
                exit_loop = True

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_THREE, ORTANT
import numpy as np


alpha = 4.256

for N in range(10, 100):
    myProblem = SAT(None, so_file_name, n=N, alpha=alpha, rhs_type=RHS_TYPE_THREE)
    N, M = myProblem.number_of_variables, myProblem.number_of_clauses
    myProblem.write_problem_to_file('SAT_problems\\benchmark4.256\\random3SATn'+str(N)+'M'+str(M))


In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_THREE, ORTANT
import numpy as np

so_file_name = 'c_libs/cSat.so'
myProblem = SAT(None, so_file_name, n=75, alpha = 4.256, rhs_type=3)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses
init_s =  2*np.random.rand(N) - np.ones(N)

solver = CTD(myProblem, initial_s=init_s, random_aux=False)
solver.fast_solve(t_max=500, solver_type='LSODA', exit_type=ORTANT)

print("Max aux:{0}".format(max(solver.sol.y[N:,-1])))
plot_traj(solver.sol, myProblem.number_of_variables, True)
plot_aux(solver.sol, N, True)

#myProblem.write_problem_to_file('SAT_problems\\random3SATn'+str(N)+'M'+str(M)+'S'+str(len(myProblem.all_solutions())))

In [ ]:
myProblem.write_problem_to_file('SAT_problems\\Benchmark_problems_N75\\random3SATn'+str(N)+'M'+str(M)+'_5')

### Small $\alpha$ problem generation

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_THREE, ORTANT

so_file_name = 'c_libs/cSat.so'

for idx in range(50):
    myProblem = None
    myProblem = SAT(None, so_file_name, n=200, alpha=2.132, rhs_type=RHS_TYPE_THREE, planted=None)
    N, M = myProblem.number_of_variables, myProblem.number_of_clauses
    myProblem.write_problem_to_file('C:\\Projects\\cppSAT\pySat\\SAT_problems\\small_alpha_N200\\random3SATn'+str(N)+'M'+str(M)+'idx'+str(idx))


### Validity checking for small $\alpha$ 

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_THREE, ORTANT
import copy
import numpy as np

so_file_name = 'c_libs/cSat.so'
solvers = []

for idx in range(10):
    N, M = 200, 427
    myProblem, solver = None, None
    myProblem = SAT('C:\\Projects\\cppSAT\pySat\\SAT_problems\\small_alpha_N200\\random3SATn'+str(N)+'M'+str(M)+'idx'+str(idx)+'.cnf', so_file_name, rhs_type=3, lmbd=0.4)
    init_s = 2*np.random.rand(N) - np.ones(N)
    solver = CTD(myProblem, initial_s=init_s, random_aux=False, initial_aux=np.ones(M))
    solver.fast_solve(t_max=75, solver_type='RK45', exit_type=ORTANT)
    solvers.append(solver)

In [ ]:
trajs = []
for solver in solvers:
    t, s = solver.get_satisfied_C_of_t()
    trajs.append((t, [elem/M for elem in s]))

plot_C_of_t(*trajs)

### Pruning check

In [ ]:
from pySAT import SAT, CTD, ORTANT
import numpy as np

so_file_name = 'c_libs/cSat.so'
myProblem = SAT("C:\\Projects\\cppSAT\\pySat\\SAT_problems\\benchmark20\\random3SATn20M85S2.cnf", so_file_name, rhs_type=10)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses

init_s = 2*np.random.rand(N) - np.ones(N)

solver = CTD(myProblem, initial_s=init_s, random_aux=False)
solver.fast_solve(t_max=5.0, solver_type='LSODA', exit_type=ORTANT)

final_b_mns = np.array([traj[-1] for traj in solver.sol.y])[N:]

In [ ]:
prune_percent = 53

threshold = np.percentile(final_b_mns, 100-prune_percent)
initial_baux = np.where(final_b_mns >= threshold, 1.0, 0.0)

for idx, bmn in enumerate(initial_baux):
    m = int(idx/M)
    n = idx % M
    if m == n:
        initial_baux[idx] = 1.0

prune_percent = int(100* sum(initial_baux)/len(initial_baux))

print(sum(initial_baux))
print(len(initial_baux))
print(prune_percent)
print(final_b_mns)

### Egyéb


In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_THREE, RHS_TYPE_ONE, RHS_TYPE_TWO, ORTANT
import numpy as np

so_file_name = 'c_libs/cSat.so'
solution_time = 0.0
while solution_time < 110.0:
    nbr_cluster = 0
    myProblem = None
    while(not (nbr_cluster == 3 or nbr_cluster == 4)):
        myProblem = SAT(None, so_file_name, n=13, alpha=4.77, rhs_type = RHS_TYPE_THREE)
        nbr_cluster = len(myProblem.get_clusters())
        nbr_sol = len(myProblem.all_solutions())
    N, M = myProblem.number_of_variables, myProblem.number_of_clauses
    init_s = [0.5846424456892467, 0.28855730591917617, -0.765485967168831, -0.19757191008885022, 0.07115735554663072, 0.8756276995661012, 0.6118210887924771, 0.5940679228111643, -0.33385990029898327,
            -0.6428940799260097, -0.053791272109619204, -0.7058511794075033, 0.5527736842134574, -0.8782685890278985, 0.29380377582167916, -0.8888067203337626, -0.4154169832230892, 0.17095162610908043,
            0.2573696988413323, -0.13771668086566802, -0.8328769256466353, -0.23920763628682162, -0.8275018021573082, -0.7581165958321621, 0.0735767709459334, 0.5068227819503663, -0.5123524411832288,
            -0.5013787551546678, -0.9948890032728812, -0.6047441113799457, 0.6911652631178293, -0.2190930534199227, -0.7662485185524224, 0.4084055267483786, -0.6192982256437018, -0.18542284167545775,
            0.43799359902439416, -0.8178673956450011, 0.017592254409698693, 0.882608207989791]
    init_s = init_s[0:N]
    solver = CTD(myProblem, initial_s=init_s, random_aux=False)
    solver.fast_solve(t_max=400, solver_type='BDF', exit_type=ORTANT)
    solution_time = solver.sol.t[-1]
    print('Solution time {0}'.format(solution_time))
plot_traj(solver.sol, myProblem.number_of_variables, hide_legends=True )
print('Number of solutions {0}, with alpha {1}'.format(nbr_sol, myProblem.get_alpha()))
print('Clusters: {0}'.format(myProblem.get_clusters()))

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_THREE, RHS_TYPE_ONE, RHS_TYPE_TWO, ORTANT
import numpy as np
from random import random

so_file_name = 'c_libs/cSat.so'

#myProblem = SAT("random3SATn20a4.57.cnf", so_file_name, rhs_type = RHS_TYPE_TWO)
myProblem = SAT(None, so_file_name, n=26, alpha=4.3, rhs_type = RHS_TYPE_TWO)
myProblem.remove_variable(myProblem.smallest_variable())
N, M = myProblem.number_of_variables, myProblem.number_of_clauses

absolute_tolerances = [10e-8, 10e-7, 10e-6, 10e-5, 10e-4]
maxt = 150
datas = {}

for a_toll in absolute_tolerances:
    sol_times = []
    for point_idx in range(75):
        rand_init = np.array([random() for i in range(N)])
        solver = CTD(myProblem, initial_s=rand_init, random_aux=False)
        solver.fast_solve(t_max=maxt, solver_type='RK45', exit_type=ORTANT, atol=a_toll)
        if solver.solution_time is not None:
            sol_times.append(solver.solution_time)
        else:
            sol_times.append(maxt)
    datas[a_toll] = sol_times

plot_error_effect(datas, max_time=maxt, number_of_points=50)   

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_THREE, RHS_TYPE_ONE, RHS_TYPE_TWO, ORTANT, CONVERGENCE_RADIUS
import numpy as np

location = 'C:\\Users\\vizke\\AppData\\Local\\Packages\\CanonicalGroupLimited.UbuntuonWindows_79rhkp1fndgsc\\LocalState\\rootfs\home\\aron\miniSAT\\'
so_file_name = 'c_libs/cSat.so'
prob_file_name = 'random3SATn20a4.26.cnf'

#myProblem2 = SAT(location + prob_file_name, so_file_name, rhs_type = RHS_TYPE_THREE)
myProblem2 = SAT(None, so_file_name, n=45, rhs_type = RHS_TYPE_THREE)
N, M = myProblem2.number_of_variables, myProblem2.number_of_clauses

myProblem2.write_problem_to_file(location + 'random3SATn45a' + str(myProblem2.get_alpha()))
print(myProblem2.get_alpha())
#print(myProblem2.all_solutions())

In [ ]:
init_s = 2 * np.random.rand(N) - np.ones(N)
solver2 = CTD(myProblem2, initial_s=init_s, random_aux=False)
solver2.fast_solve(t_max=750, solver_type='RK45', exit_type=ORTANT)
# print(myProblem2.get_alpha())
plot_traj(solver2.sol, N, True)
# print(myProblem2.all_solutions())

In [ ]:
#myProblem2.write_problem_to_file(location + 'random3SATn'+str(N)+'a'+str(myProblem2.get_alpha()))
myProblem.write_problem_to_file('random3SATn'+str(N)+'a'+str(myProblem.get_alpha()))

In [ ]:
import numpy as np

#clusters = myProblem2.get_clusters()

ortants = ['start']
for pnt_idx in range(len(solver2.sol.y[0])):
    r_point = np.zeros(N)
    bit_string = ''
    for var_idx in range(len(solver2.sol.y)):
        if var_idx < N:
            r_point[var_idx] = solver2.sol.y[var_idx][pnt_idx]
    
    for coord in r_point:
        if coord >= 0.0:
            bit_string += '1'
        else:
            bit_string += '0'
    
    if ortants[-1] != bit_string:
        ortants.append(bit_string)
ortants.remove('start')

print(ortants)

# with open(prob_file_name + '.csv', 'w') as csv_file:
#     csv_file.write('Ortant,Cluster,Solution,\n')
#     for ortant in ortants:
#         sol_idx = 0
#         ortant_idx = 0
#         for keys, vals in clusters.items():
#             if ortant in vals:
#                 ortant_idx = keys + 1
#                 sol_idx = myProblem.get_solution_index(ortant)
#         csv_file.write("'"+ ortant +"'"+  ',' + str(ortant_idx) + ',' + str(sol_idx) + ',\n')

    

In [ ]:
dicts= [ {1: 4937, 2: 142, 3: 24, 4: 1}, {1: 7051, 2: 139, 3: 4}, {1: 12344, 2: 591, 3: 121, 4: 1}, {1: 24141, 3: 408, 4: 144, 2: 2041, 7: 24, 5: 24} ]

list_names = {'a=3.9', 'a=4.24', 'a=4.4', 'a=4.9'}

In [ ]:
myProblem3 = SAT('C:\Projects\cppSAT\pySat\SAT_problems\\random3SATn20a4.35.cnf', so_file_name, rhs_type = RHS_TYPE_THREE)
myProblem3.all_solutions()

In [ ]:
from matplotlib import pyplot as plt

ortant_set = set(ortants)

xs1 = [int(element, 2) for element in ortant_set if not myProblem2.check_solution([True if x == '1' else False for x in element])]
ys1 = [ortants.count(elem) for elem in ortant_set if not myProblem2.check_solution([True if x == '1' else False for x in elem])]
xs2 = [int(element, 2) for element in ortant_set if myProblem2.check_solution([True if x == '1' else False for x in element])]
ys2 = [ortants.count(elem) for elem in ortant_set if myProblem2.check_solution([True if x == '1' else False for x in elem])]

#plt.plot(to_plot, 'r+')
plt.plot(xs1, ys1, 'bx')
plt.plot(xs2, ys2, 'r+')
plt.grid(True)
plt.title('Histogram of analog trajectory for problem with n=40')
plt.ylabel('Multiplicity of ortant')
plt.xlabel('Decimal number of ortant')
plt.show()

In [ ]:
from pySAT import SAT, CTD
import numpy as np
from scipy import optimize

from pySAT import SAT, CTD
import numpy as np

cnf_file = "C:\Projects\cppSAT\pySat\SAT_problems\shubha_small_2.cnf"
cnf_file = "C:\Projects\cppSAT\pySat\SAT_problems\\tiny.cnf"
so_file_name = 'c_libs/cSat.so'
myProblem = SAT(cnf_file, so_file_name, rhs_type=1)
def wrapper_fnc(x, i):
    return myProblem.rhs(0, x)[i]


N, M = myProblem.number_of_variables, myProblem.number_of_clauses
u0 = np.ones(N+M)
init_s = [0.3934262373, 0.7150070725, 0.7482993410, 0.8682550782, 0.3400653559, 0.8864542655, 0.4565491083, 0.2409856937, 0.3712098457, 0.9783567466, 0.6103133947, 0.9705718923, 0.3622861688, 0.5380535901, 0.05820786103, 0.1242846544, 0.4328300679, 0.7575798495, 0.8292365090, 0.6228237150]
init_s = init_s[0:N]
u0[0:N] = np.array(init_s)
eps = np.sqrt(np.finfo(float).eps)

print("dy/dt: {0}".format(myProblem.rhs(0.0, u0)))
J = [[] for i in range(N+M)]
for i in range(N+M):
    J[i] = optimize.approx_fprime(u0, wrapper_fnc, [eps for k in range(N+M)], i)
print("Approximate Jacobian: {0}".format(J))
print("c-calculated Jakobian: {0}".format(myProblem.Jakobian(u0)))


In [ ]:

l= [bin(x)[2:].rjust(3, '0') for x in range(2**3)]
[True if kar == '1' else False for kar in l[3]]


In [ ]:
from pySAT import SAT
import numpy as np
import matplotlib.pyplot as plt

#myProblem = SAT('chaotic_SAT/8770.903495788574random3SATn13c59.cnf')
#myProblem = SAT('chaotic_SAT/small1.cnf')
myProblem = SAT('SAT_problems/shubha_small_2.cnf', None)

img_size = 1024

run_times = np.array([[0.0 for j in range(img_size)] for i in range(img_size)])
solutions = np.array([[0 for j in range(img_size)] for i in range(img_size)])

file_name = '_shubha2_sat1_zoom.out'

with open('results/'+ str(img_size) + file_name, 'r') as resultfile:
    lines = resultfile.readlines()
    l_1 = 'Loading python/3.7.3\n'
    l_2 = '  Loading requirement: tcl/8.6.8 gcc/8.3.0\n'
    while(l_1 in lines):
        lines.remove(l_1)
    while(l_2 in lines):
        lines.remove(l_2)
    for k in range(int(len(lines)/3)):
        i = int(lines[k*3].split(' ')[1])
        j = int(lines[k*3].split(' ')[3])
        sol = lines[k*3+1].split(' ')[1].replace('\n', '')
        t = float(lines[k*3+2].split(' ')[1])
        
        try:
            sol_nbr = myProblem.all_solutions().index(sol)
        except Exception as err:
            #print(err)
            sol_nbr = len(myProblem.all_solutions())
        solutions[i][j] = sol_nbr
        run_times[i, j] = np.log(t+1)

#Normalizing values
maximum = max([max(x) for x in run_times])
for i, row in enumerate(run_times):
    for j, elem in enumerate(row):
        run_times[i, j] /= maximum

print(myProblem.number_of_clauses)
plt.xlabel("s1")
plt.ylabel('s2')
plt.tick_params(axis='both', which='both', bottom=False, left=False, labelbottom = False, labelleft = False)
# plt.imshow(run_times, cmap='Blues', resample=False)
# plt.savefig('results/basin_boundaries/'+ str(img_size) + file_name + 'logtime.png', dpi=700)
plt.imshow(solutions, cmap='Accent', interpolation='nearest')
#plt.savefig('results/basin_boundaries/'+ str(img_size) + file_name + 'boundary.png', dpi=700)

    

In [ ]:
myProblem = SAT('chaotic_SAT/shubha_small_2.cnf')

img_size = 512

run_times = []
solutions = []

file_name = '_shubha2_sat1_4.out'

with open('results/'+ str(img_size) + file_name, 'r') as resultfile:
    lines = resultfile.readlines()
    l_1 = 'Loading python/3.7.3\n'
    l_2 = '  Loading requirement: tcl/8.6.8 gcc/8.3.0\n'
    while(l_1 in lines):
        lines.remove(l_1)
    while(l_2 in lines):
        lines.remove(l_2)
    for k in range(int(len(lines)/3)):
        i = int(lines[k*3].split(' ')[1])
        j = int(lines[k*3].split(' ')[3])
        t = float(lines[k*3+2].split(' ')[1])
        

        run_times.append(t)
        solutions.append((i,j))

s1s = np.linspace(-0.9999, 0.9999, img_size)
tmax = max(run_times)
print(tmax)
(mi, mj) = solutions[run_times.index(tmax)]
print((mi, mj))
print((s1s[mi], s1s[mj]))

In [ ]:
def basin_entropy(matrix, grid_resolution = 5, number_of_solutions = None):
    img_size = len(matrix)
    N = 0
    Si = []
    if not number_of_solutions:
        number_of_solutions = max([max(row) for row in matrix])
    for i in range(img_size):
        for j in range(img_size):
            if i % grid_resolution == 0 and j % grid_resolution == 0:
                N += 1
                ps = np.zeros(number_of_solutions)
                for k in range(grid_resolution):
                    for l in range(grid_resolution):
                        ps[ matrix[i-k][j-l]-1 ] += 1
                ps = [elem / grid_resolution**2 for elem in ps ]
                Si.append(sum([pij*np.log(1/pij) if pij != 0 else 0 for pij in ps]))

    return sum(Si)/N

def basin_boundary_entropy(matrix, grid_resolution = 5, number_of_solutions = None):
    img_size = len(matrix)
    N = 0
    Si = []
    if not number_of_solutions:
        number_of_solutions = max([max(row) for row in matrix])
    for i in range(img_size):
        for j in range(img_size):
            if i % grid_resolution == 0 and j % grid_resolution == 0:
                ps = np.zeros(number_of_solutions)
                for k in range(grid_resolution):
                    for l in range(grid_resolution):
                        ps[ matrix[i-k][j-l]-1 ] += 1
                number_of_colors = sum([1 if elem > 0 else 0 for elem in ps])
                if number_of_colors > 1:
                    N += 1
                ps = [elem / grid_resolution**2 for elem in ps ]
                Si.append(sum([pij*np.log(1/pij) if pij != 0 else 0 for pij in ps]))

    return sum(Si)/N

print(np.log(2))
print(basin_boundary_entropy(solutions))
                    

### Calculating the escape rate (kappa)

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_ONE, ORTANT, HYPER_SPHERE
import numpy as np

so_file_name = 'c_libs/cSat.so'
myProblem = SAT('SAT_problems/benchmark4.256/random3SATn60M256.cnf', so_file_name, rhs_type=RHS_TYPE_ONE)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses

In [ ]:
number_of_initial_points = 50
initial_points = [2*np.random.rand(N) - np.ones(N) for i in range(number_of_initial_points)]

In [ ]:
escape_times = [] # List of touples, first element is the time of first escape last element is the time of last escape
max_aux_values = [] # List of touples, first element is the maximum aux at the time of first escape last element is the same at time of last escape
solver = None
for init_point in initial_points:
    solver = CTD(myProblem, initial_s=init_point, random_aux=False)
    solver.fast_solve(t_max=200, solver_type='RK45', exit_type=HYPER_SPHERE, hypersphere_radius=np.sqrt(N)*0.95)
    escape_times.append( (solver.sol.t_events[0][0], solver.sol.t_events[0][-1]) )
    max_aux_values.append( (max(solver.sol.y_events[0][0]), max(solver.sol.y_events[0][-1])) )
#print(escape_times)
#print(max_aux_values)

In [ ]:
xs_kappa_1 = np.linspace(min([elem[0] for elem in escape_times]), max([elem[0] for elem in escape_times]))
# List of the number of elements greater then t for each t in xs
ys_kappa_1 = [len([element for element in [elem[0] for elem in escape_times] if element > t])/number_of_initial_points for t in xs_kappa_1]

xs_kappa_2 = np.linspace(min([elem[1] for elem in escape_times]), max([elem[1] for elem in escape_times]))
# List of the number of elements greater then t for each t in xs
ys_kappa_2 = [len([element for element in [elem[1] for elem in escape_times] if element > t])/number_of_initial_points for t in xs_kappa_2]

# Fitting exponential decay
kappa_1, const_1 = np.polyfit(xs_kappa_1[:-1], np.log(ys_kappa_1[:-1]), 1, w=np.sqrt(ys_kappa_1[:-1]))
kappa_2, const_2 = np.polyfit(xs_kappa_2[:-1], np.log(ys_kappa_2[:-1]), 1, w=np.sqrt(ys_kappa_2[:-1]))

print(kappa_2)

In [ ]:
import matplotlib.pyplot as plt

with plt.style.context('ggplot'):#'seaborn-darkgrid'):
    #plt.grid(True)
    #plt.title('Escaped rate with average aux_max {:.4f}'.format(sum(max_aux_values)/len(max_aux_values)))
    plt.plot(xs_kappa_1, ys_kappa_1, '+', label="simulation data, first escape")#, first escape")
    plt.plot(xs_kappa_1, [np.exp(const_1+kappa_1*element) for element in xs_kappa_1], label="$\kappa$={:.4f}".format(-kappa_1))
    plt.plot(xs_kappa_2, ys_kappa_2, '+', label="simulation data, last escape")
    plt.plot(xs_kappa_2, [np.exp(const_2+kappa_2*element) for element in xs_kappa_2], label="$\kappa_1 =${:.4f}".format(-kappa_2))
    plt.xlabel("Analog time")
    plt.yscale("log")
    plt.ylabel("Fraction of points in hypersphere")
    #plt.yscale("log")
    plt.legend()
    plt.plot()
    #plt.savefig('kappa_1_loglin.png', dpi=350)

### Calculating fraction of solved trajectories in time (p)

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_THREE, ORTANT, HYPER_SPHERE
import numpy as np

solution_times = []
max_aux_values2 = []
for init_point in initial_points:
    solver = CTD(myProblem, initial_s=init_point, random_aux=False)
    solver.fast_solve(t_max=75, solver_type='RK45', exit_type=ORTANT)
    solution_times.append(solver.sol.t[-1])
    max_aux_values2.append(max(solver.sol.y[-1]))

In [ ]:
xs_p = np.linspace(min(solution_times), max(solution_times), 100)
# List of the number of elements greater then t for each t in xs
ys_p = [len([element for element in solution_times if element > t])/number_of_initial_points for t in xs_p]

# Fitting exponential decay
B, A = np.polyfit(xs_p[:-1], np.log(ys_p[:-1]), 1, w=np.sqrt(ys_p[:-1]))
print(A, B)

In [ ]:
import matplotlib.pyplot as plt
plt.grid(True)
plt.title('Solution rate with average aux_max {:.4f}'.format(sum(max_aux_values)/len(max_aux_values)))
plt.plot(xs_p, ys_p, label="simulation data")
plt.plot(xs_p, [np.exp(A+B*element) for element in xs_p], label="kappa:{:.4f}".format(B))
plt.xlabel("Analog time")
plt.ylabel("Fraction of trajectories yet to solve problem")
plt.yscale("log")
plt.legend()

In [ ]:
print(solution_times)
print(escape_times)

### Random initial points with infinitesimal separation

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_THREE, RHS_TYPE_FIVE, ORTANT, NEGATIVE_AUX
import numpy as np
from random import random

def normalized_random_vec(dimension):
    result = 2*np.random.rand(dimension)-np.ones(dimension)
    result /= np.linalg.norm(result)
    return result

so_file_name = 'c_libs/cSat.so'
myProblem = SAT("SAT_problems\\random3SATn15a4.266666666666667.cnf", so_file_name, rhs_type=RHS_TYPE_THREE)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses

dem_deltas = np.logspace(-17, -2, 11, endpoint=True, base=10)
number_of_random_pairs = 10

p_values = []

for delta_0 in dem_deltas:
    init_as = [np.array([2*random()-1 for i in range(N)]) for j in range(number_of_random_pairs)]
    init_bs = [init + normalized_random_vec(N) * delta_0 for init in init_as]
    same_solution = 0
    different_solution = 0

    for init_a, init_b in zip(init_as, init_bs):
        solver_a = CTD(myProblem, initial_s=init_a, random_aux=False)
        solver_b = CTD(myProblem, initial_s=init_b, random_aux=False)
        solver_a.fast_solve(t_max=500, solver_type='RK45', exit_type=ORTANT)
        solver_b.fast_solve(t_max=500, solver_type='RK45', exit_type=ORTANT)
        if solver_a.get_solution() != solver_b.get_solution():
            different_solution += 1
        else:
            same_solution += 1

    p_values.append(same_solution / (same_solution + different_solution))




In [ ]:
import matplotlib.pyplot as plt
plt.grid(True)
plt.title('Spin variables')

dem_deltas = np.logspace(-17, -2, 11, endpoint=True, base=10)
p_values = np.random.rand(len(dem_deltas))
plt.xscale("log")
plt.xlabel("Initial condition separation (log scale)")
plt.ylabel("Fraction of trajectories going into the same solution")
plt.plot(dem_deltas, p_values)
plt.show()

### Egyéb 2

In [ ]:
from pySAT import SAT, CTD, ORTANT, HYPER_SPHERE, CONVERGENCE_RADIUS
import numpy as np

so_file_name = 'c_libs/cSat.so'
myProblem = SAT('SAT_problems/Benchmark_problems_N75/random3SATn75M320_1.cnf', so_file_name, n = 75, rhs_type=3, lmbd=1.1)
#myProblem = SAT('SAT_problems/benchmark20/random3SATn20M121S1.cnf', so_file_name, n = 75, rhs_type=3, lmbd=1.1)

N, M = myProblem.number_of_variables, myProblem.number_of_clauses

In [ ]:
init_s = 2*np.random.rand(N) - np.ones(N)
init_s = np.array([0.99, -0.99, -0.99, -0.99, 0.99, -0.99, -0.99, 0.99, 0.99, 0.99, 0.99, 0.99, -0.99, -0.99, 0.99, -0.99, -0.99, -0.99, -0.99, 0.99, -0.99, 0.99, 0.99, 0.99, -0.99, 0.99, 0.99, 0.99, 0.99, 0.99, -0.99, 0.99, 0.99, -0.99, 0.99, 0.99, 0.99, -0.99, -0.99, 0.99, 0.99, -0.99, 0.99, -0.99, -0.99, -0.99, -0.99, -0.99, -0.99, -0.99, -0.99, 0.99, -0.99, -0.99, 0.99, -0.99, 0.99, -0.99, 0.99, -0.99, -0.99, 0.99, 0.99, -0.99, 0.99, -0.99, -0.99, -0.99, 0.99, 0.99, -0.99, -0.99, 0.99, -0.99, -0.99])

In [ ]:
solver = CTD(myProblem, initial_s=init_s, random_aux=False)
solver.fast_solve(t_max=40, solver_type='RK45', exit_type=ORTANT)

In [ ]:
solver.get_ortant_path()

In [ ]:
plot_traj_js(solver, False)

In [ ]:
plot_aux_js(solver, False)

In [ ]:
t, s = solver.get_satisfied_C_of_t()
plot_C_of_t((t, [elem/M for elem in s]))

In [ ]:
points_to_plot = dict()
points_to_plot[75] = []
points_to_plot[20] = []
points_to_plot[50] = []
points_to_plot[100] = []

In [ ]:
points_to_plot[75] 

## Aux failure statistics

In [ ]:
import os
from pySAT import SAT, CTD, ORTANT, Warning_propagator
import numpy as np

traj_path= 'results\\AuxFail'
solvers = []
so_file_name = "c_libs/cSAT.so"
myProblem = SAT("SAT_problems\\SATLIB_Benchmark_problems_N50\\uf50-06.cnf", so_file_name, rhs_type=3)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses

not_solved_nbr = 0
# Iterate through files in the directory
for filename in os.listdir(traj_path):
    # Check if the file is a regular file (not a directory)
    if os.path.isfile(os.path.join(traj_path, filename)):
        #char1 = filename[0]
        #char2 = filename[1]
        #nbr = int(char1) if not char2.isdigit() else int(char1 + char2)
        print("opening {0}:".format(filename))
        solver = CTD.load_sol_from_file(os.path.join(traj_path, filename), myProblem)
        t_final = solver.sol.t[-1]
        print(t_final)
        if t_final >= 420.0:
            not_solved_nbr += 1
            solvers.append(solver)

print("The number of unsolved instances:{0}".format(not_solved_nbr))


In [ ]:
def get_top_r_time_ratio(solver, r, transient_cutoff_time = 100):
    
    def get_rank_order(solver):
        # Get the number of vectors and time points
        num_time_points = solver.sol.t.shape[0]

        # Initialize an empty list to store the rank orders
        rank_orders = []

        # Iterate over each time point
        for t in range(num_time_points):
            # Get the vector at the current time point
            vector = solver.sol.y[N:, t]

            # Get the indices that would sort the vector
            indices = sorted(range(len(vector)), key=lambda i: vector[i])

            # Add the rank order of indices to the list
            rank_orders.append(indices)

        return rank_orders


    num_time_points = solver.sol.t.shape[0]
    result = np.zeros(solver.problem.number_of_clauses)
    rank_order = get_rank_order(solver)

    total_time = 0.0#solver.sol.t[-1] - transient_cutoff_time

    # Iterate over each time point
    for t_i in range(num_time_points-1):
        if solver.sol.t[t_i] > transient_cutoff_time:
            dt = solver.sol.t[t_i +1] - solver.sol.t[t_i]
            for j in range(r):
                top_r_idx = rank_order[t_i][-1-j]
                result[top_r_idx] += dt
            total_time += dt

    return result / (r*total_time)
        
# rank order as a function of time
# Mennyi időt tolt egy mondat a top 10 ben arány
# Az első ~100 időt eldobni

In [ ]:
integrated_toplist = np.zeros(M)
nbr_runs = 61
for i in range(nbr_runs):
    ith_toplist = get_top_r_time_ratio(solvers[i], r=10)
    integrated_toplist += ith_toplist

integrated_toplist = integrated_toplist / nbr_runs


sorted_indices = np.argsort(integrated_toplist)[::-1]
sorted_numbers = integrated_toplist[sorted_indices]

In [ ]:
import matplotlib.pyplot as plt

# Plotting the bar plot
plt.bar(range(M), sorted_numbers)

# Adding labels and title
plt.xlabel('Ordered clause index')
plt.ylabel('Fraction of time spent in top r=10')
plt.title('Bar Plot of time spent in top r=10 by aux')
plt.grid(True)

# Display the plot
plt.show()


Calculating DTW distances between $K_n(t)$ series

In [ ]:
#from tslearn.metrics import dtw

from ctypes import CDLL, POINTER, c_double, c_int
import numpy as np

matrices = []
for i in range(10):
    da_solver = solvers[i]

    k_m_series = np.empty( (M, len(da_solver.sol.t)) )
    for t_idx, t in enumerate(da_solver.sol.t):
        s = da_solver.sol.y[:N, t_idx]

        k = np.empty(M, dtype=np.double)
        k_pointer = k.ctypes.data_as(POINTER(c_double))

        state = s.astype(np.double)
        s_pointer = state.ctypes.data_as(POINTER(c_double))

        myProblem.cSAT_functions.precompute_km(N, M, myProblem.clause_matrix_pointer, s_pointer, k_pointer)
        k_m_series[:, t_idx] = k

    distance_matrix = np.empty((M, M))
    for m in range(M):
        for n in range(M):
            if n >= m:
                series_n = k_m_series[n, :]
                series_m = k_m_series[m, :]
                #dtw_nm_distance = dtw(series_n, series_m)
                #distance_matrix[n, m] = dtw_nm_distance
                #distance_matrix[m, n] = dtw_nm_distance

                # no comment
                mean_m = sum(series_m)/len(series_m)
                mean_n = sum(series_n)/len(series_n)
                
                C_mn = 0.0
                for t_idx, t in enumerate(da_solver.sol.t):
                    C_mn += (series_m[t_idx] - mean_m)*(series_n[t_idx] - mean_n)
                C_mn *= 1/(len(da_solver.sol.t)-1)

                distance_matrix[n, m] = C_mn
                distance_matrix[m, n] = C_mn
            #elif n==m:
            #    distance_matrix[m, n] = 0.0
    matrices.append(distance_matrix)

In [ ]:
to_be_plotted = np.zeros((M, M))
for matrix in matrices:
    to_be_plotted += matrix

from scipy.cluster import hierarchy
import numpy as np

from scipy.cluster import hierarchy
import numpy as np

def cluster_matrix(matrix):
    # Compute hierarchical clustering for rows
    row_clusters = hierarchy.linkage(matrix, method='average')
    
    # Get row dendrogram leaf order
    row_dendrogram = hierarchy.dendrogram(row_clusters, no_plot=False)
    
    # Reorder rows based on dendrogram leaf order
    clustered_matrix = matrix[row_dendrogram['leaves'], :]
    
    # Reorder columns based on row dendrogram leaf order
    clustered_matrix = clustered_matrix[:, row_dendrogram['leaves']]
    
    return clustered_matrix

plot_matrix_js(cluster_matrix(to_be_plotted), title="Some matrix")

In [ ]:
def compute_cophenetic_correlation(matrix):
    from scipy.cluster import hierarchy
    from scipy.spatial.distance import pdist
    
    # Compute pairwise distances
    distances = pdist(matrix)
    
    # Perform hierarchical clustering
    linkage_matrix = hierarchy.linkage(distances, method='average')
    
    # Compute cophenetic correlation coefficient
    c, _ = hierarchy.cophenet(linkage_matrix, distances)
    
    return c
# Example usage:
cophenetic_correlation = compute_cophenetic_correlation(to_be_plotted)
print("Cophenetic Correlation Coefficient:", cophenetic_correlation)

### Restart

In [ ]:
import copy

solver = copy.copy(solvers[0])

In [ ]:
solver.continue_solution(0.4)

In [ ]:
t, s = solver.get_satisfied_C_of_t()
plot_C_of_t((t, [elem/M for elem in s]))

In [ ]:
plot_sumk_js(solver)

In [ ]:
solver.problem.c[23,23]

In [ ]:
plot_traj_js(solver)

In [ ]:
def my_fnc(solver, time_distance_flag = None):
    import plotly.graph_objects as go
    import numpy as np
    from ctypes import CDLL, POINTER, c_double, c_int, c_char

    fig = go.Figure()
    N = solver.problem.number_of_variables
    M = solver.problem.number_of_clauses
    if time_distance_flag:
        my_x = solver.get_sol_length()
    else:
        my_x = solver.sol.t

    s_t = solver.sol.y[:N, :]
    
    
    k_ts = np.empty( (M, len(solver.sol.t)) )
    for idx_t, s in enumerate(s_t):
        if solver.problem.cSAT_functions is not None:
            k = np.empty(M, dtype=np.double)
            k_pointer = k.ctypes.data_as(POINTER(c_double))
            state = s.astype(np.double)
            s_pointer = state.ctypes.data_as(POINTER(c_double))

            solver.problem.cSAT_functions.precompute_km(N, M, solver.problem.clause_matrix_pointer, s_pointer, k_pointer)
            k_ts[:M, idx_t] = k

    
    fig.add_trace(go.Scatter(x=my_x, y=k_t, name='my name', mode='lines'))
    
    # if time_distance_flag:
    #     fig.update_xaxes(title_text="Trajectory length", type="linear")
    # else:
    #     fig.update_xaxes(title_text="Continuous time", type="linear")
    
    # fig.update_yaxes(title_text="Potential value")

    # fig.show()

my_fnc(solver)

In [ ]:
solver.sol.y[11, -2]

In [ ]:
last_s = solver.sol.y[:N,-2]
last_aux = solver.sol.y[N:,-2]
x = np.concatenate((last_s, last_aux), axis=None)
dx = solver.problem.rhs(solver.sol.t[-2], x)

In [ ]:
for i in range(N):
    s_sign = '+' if x[i] > 0 else '-'
    ds_sign = '+' if dx[i] > 0 else '-'
    print("s{2}:{0},   ds{2}:{1}".format(s_sign, ds_sign, i))

In [ ]:
def switch_largest_smallest(array):
    # Sort the array
    sorted_array = sorted(array)
    n = len(sorted_array)
    
    # Initialize the result array
    result_array = array.copy()
    
    # Swap elements pairwise
    for i in range(n // 2):
        result_array[array.index(sorted_array[i])] = sorted_array[n - i - 1]
        result_array[array.index(sorted_array[n - i - 1])] = sorted_array[i]
    
    return result_array

# Example usage:
original_array = [3.7, 8.1, 2.9, 6.4, 5.2]
result = switch_largest_smallest(original_array)
print(result)


In [ ]:
def indices_above_threshold(arr, threshold):
    """Returns (aparently ordered) list of indeces of the elements larger than threshold x max
    Indices start from one!
    """
    max_val = np.max(arr)
    threshold_val = threshold * max_val
    above_threshold_indices = np.where(arr > threshold_val)
    #sorted_indices = np.argsort(arr[above_threshold_indices])[::-1]
    #return above_threshold_indices[sorted_indices]
    return [elem + 1 for elem in above_threshold_indices[0]]

troubled_histogram = [0 for _ in range(M)]
for solver in solvers:
    trouble_clauses = indices_above_threshold(solver.sol.y[N:,-1], 0.5)
    for i in range(M):
        if i in trouble_clauses:
            troubled_histogram[i] += 1

In [ ]:
import matplotlib.pyplot as plt

# Plotting the bar plot
plt.bar(range(M), troubled_histogram)

# Adding labels and title
plt.xlabel('Clause index')
plt.ylabel('Frequencies')
plt.title('Bar Plot of Frequencies')
plt.yticks(range(min(troubled_histogram), max(troubled_histogram)+1))
plt.grid(True)

# Display the plot
plt.show()


In [ ]:
import matplotlib.pyplot as plt

# Zip the clause indices and troubled_histogram together
zipped_data = zip(range(M), troubled_histogram)

# Sort the zipped data based on the troubled_histogram values
sorted_data = sorted(zipped_data, key=lambda x: x[1], reverse=True)

# Unzip the sorted data to get sorted_clause_indices and sorted_troubled_histogram
sorted_clause_indices, sorted_troubled_histogram = zip(*sorted_data)

# Plotting the bar plot with sorted data
plt.bar(range(len(sorted_clause_indices)), sorted_troubled_histogram)

# Adding labels and title
plt.xlabel('Ordered clause index')
plt.ylabel('Frequencies')
plt.title('Bar Plot of Frequencies')
plt.yticks(range(min(troubled_histogram), max(troubled_histogram)+1))
plt.grid(True)

# Display the plot
plt.show()


## Exponential memory supression 

$$
\frac{da_m}{dt} = a_m \left[ -\lambda ln\left( \frac{a_m}{a_{m, 0}} \right) + K_m \right]
$$

### Example run

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_EIGHT, ORTANT, HYPER_SPHERE
import numpy as np

so_file_name = 'c_libs/cSat.so'
myProblem = myProblem = SAT('SAT_problems/random3SATn40a4.512195121951219.cnf', so_file_name, rhs_type=3, lmbd=0.1)

N, M = myProblem.number_of_variables, myProblem.number_of_clauses

In [ ]:
init_s = 2*np.random.rand(N) - np.ones(N)
init_a = 2*np.ones(M)

In [ ]:
myProblem.lmdb = 0.05

solver = CTD(myProblem, initial_s=init_s, random_aux=False, initial_aux=init_a)
solver.fast_solve(t_max=50, solver_type='LSODA', exit_type=ORTANT)


In [ ]:
plot_traj_js(solver, False)

In [ ]:
plot_aux_js(solver)

In [ ]:
t, s = solver.get_satisfied_C_of_t()
plot_C_of_t((t, [elem/M for elem in s]))

### Accuracy tests

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_EIGHT, ORTANT, HYPER_SPHERE
import numpy as np

so_file_name = 'c_libs/cSat.so'
myProblem1 = SAT('SAT_problems/random3SATn15a4.266666666666667.cnf', so_file_name, rhs_type=8)
myProblem2 = SAT('SAT_problems/random3SATn15a4.266666666666667.cnf', None, rhs_type=8)
N, M = myProblem1.number_of_variables, myProblem2.number_of_clauses


init_s = 2*np.random.rand(N) - np.ones(N)
init_a = np.ones(M)

step = myProblem1.rhs(0, np.concatenate((init_s, init_a), axis=None))-myProblem2.rhs(0, np.concatenate((init_s, init_a), axis=None))

print(sum(step[0:N]))

In [ ]:
#init_s = 2*np.random.rand(N) - np.ones(N)
myProblem1.lmdb = 0.01

solver1 = CTD(myProblem1, initial_s=init_s, random_aux=False)
solver1.fast_solve(t_max=250, solver_type='BDF', exit_type=ORTANT)

#solver2 = CTD(myProblem2, initial_s=init_s, random_aux=False)
#solver2.fast_solve(t_max=50, solver_type='RK45', exit_type=ORTANT)

plot_traj(solver1.sol, N, True)
plot_aux(solver1.sol, N, True)
#plot_traj(solver2.sol, N, True)

### Optimal lambda search

In [ ]:
# Tabu search

def tabu_search(objective_function, getNeighbours, stopping_condition, initial_param_value = 0.0, max_tabu_size = 100):
    """Finds the maximum of the objective function"""
    local_best_candidate = initial_param_value
    seen_best_candidate = initial_param_value
    tabu_list = []
    tabu_list.append(local_best_candidate)
    while(not stopping_condition(objective_function, seen_best_candidate)):
        neighbours = getNeighbours(objective_function, local_best_candidate)
        for candidate in neighbours:
            if not candidate in tabu_list and objective_function(candidate) > objective_function(local_best_candidate):
                local_best_candidate = candidate
            if objective_function(local_best_candidate) > objective_function(seen_best_candidate):
                seen_best_candidate = local_best_candidate
            tabu_list.append(local_best_candidate)
            if len(tabu_list) > max_tabu_size:
                tabu_list.pop(0)

    return local_best_candidate

def getNeig1D(func, param, resolution = 0.01):
    return [param + resolution, param - resolution]


In [ ]:
def stopSin(func, value):
    if func(value) > 0.99999:
        return True
    else :
        return False
obj_fnc = lambda x : (-x *x -6*x)/9
tabu_search(obj_fnc, getNeig1D, stopSin)

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_EIGHT, ORTANT, HYPER_SPHERE
import numpy as np

so_file_name = 'c_libs/cSat.so'
myProblem = SAT('SAT_problems/random3SATn15a4.266666666666667.cnf', so_file_name, rhs_type=RHS_TYPE_EIGHT)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses

inits = [2*np.random.rand(N) - np.ones(N) for i in range(50)]
results = []
lambdas = np.linspace(0.0, 0.05, 10)
for lambda_candidate in lambdas:
    total_TTS = 0.0
    
    myProblem.lmdb = lambda_candidate
    for init in inits:
        solver = CTD(myProblem, initial_s=init, random_aux=False)
        solver.fast_solve(t_max=100, solver_type='LSODA', exit_type=ORTANT)
        total_TTS += solver.get_sol_time()
    average_time = total_TTS/len(inits)
    print("Simulation with lambda {0} finished, with average TTS {1}".format(myProblem.lmdb, average_time))
    results.append(average_time)

In [ ]:
import matplotlib.pyplot as plt

lambdas_to_be_plotted = []
aTTS_to_be_plotted = []

for i, elem in enumerate(results):
    if elem > 5.0:
        lambdas_to_be_plotted.append(lambdas[i])
        aTTS_to_be_plotted.append(elem)

plt.grid(True)
plt.title('TTS vs $\lambda$')
plt.plot(lambdas_to_be_plotted, aTTS_to_be_plotted, '+')
plt.show()

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_EIGHT, ORTANT, HYPER_SPHERE
import numpy as np

init_idx = 3

so_file_name = 'c_libs/cSat.so'
myProblem1 = SAT('SAT_problems/random3SATn15a4.266666666666667.cnf', so_file_name, rhs_type=RHS_TYPE_EIGHT)
myProblem2 = SAT('SAT_problems/random3SATn15a4.266666666666667.cnf', so_file_name, rhs_type=RHS_TYPE_EIGHT)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses
myProblem1.lmdb = 0.47368421052631576
myProblem2.lmdb = 0.07894736842105263

solver1 = CTD(myProblem1, initial_s=inits[init_idx], random_aux=False)
solver1.fast_solve(t_max=100, solver_type='LSODA', exit_type=ORTANT)
solver2 = CTD(myProblem1, initial_s=inits[init_idx], random_aux=False)
solver2.fast_solve(t_max=100, solver_type='LSODA', exit_type=ORTANT)

In [ ]:
plot_traj(solver1.sol, N, True)
plot_traj(solver2.sol, N, True)

In [ ]:
plot_aux(solver1.sol, N, True)
plot_aux(solver2.sol, N, True)

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_SEVEN, ORTANT, HYPER_SPHERE
import numpy as np

init_idx = 3

so_file_name = None# 'c_libs/cSat.so'
myProblem = SAT('SAT_problems/random3SATn15a4.266666666666667.cnf', so_file_name, rhs_type=RHS_TYPE_SEVEN)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses
myProblem.lmdb = 0.47368421052631576

solver = CTD(myProblem, initial_s=2*np.random.rand(N) - np.ones(N), random_aux=False, initial_aux=np.zeros(M))
solver.fast_solve(t_max=50, solver_type='LSODA', exit_type=ORTANT)


In [ ]:
import matplotlib.pyplot as plt
plt.grid(True)
plt.title('Drive functions')
for i, aux_var in enumerate(solver.sol.y[N:]):
    x = solver.sol.t
    y = aux_var
    plt.plot(x, y, label='s'+str(i+1))
plt.show()

# Higher order Memory


## Base equations

$$
V(s, a) = \sum_{m = 1}^M a_m  K_{m}^2
$$
$$
V(s, b) = \sum_{m,n=1}^M b_{mn} K_m K_n
$$
$$
\frac{\partial}{\partial s_i} K_m K_n = \frac{\partial  K_m}{\partial s_i} K_n + K_m \frac{\partial  K_n}{\partial s_i} 
$$

$$
\frac{\partial  K_m}{\partial s_i} = 2^{-k} \prod_{i \neq j}^N (1-c_{mj}s_j)(-c_{mi})=-c_{mi} K_{m i}
$$

$$
\frac{ds_i}{dt} =-\frac{\partial}{\partial s_i} V = \sum_{m,n}  b_{m n} \left(c_{mi} K_{mi}K_m + c_{ni} K_{ni}K_n \right)
$$
$$
\frac{d b_{m n}}{dt} = b_{m n} K_{m} K_{n}
$$

## Test

In [ ]:
from pySAT import SAT, CTD, ORTANT, Warning_propagator
import numpy as np


so_file_name = 'c_libs/cSAT.so'
myProblem = SAT("E:\\Aron\\pySat\\SAT_problems\\random3SATn15a4.266666666666667.cnf", so_file_name, rhs_type=12)
#myProblem = SAT("C:\\Projects\\cppSAT\\pySat\\SAT_problems\\SATLIB_Benchmark_problems_N50\\uf50-06.cnf", so_file_name, lmbd = 0.05, rhs_type=12)
#myProblem2 = SAT("C:\\Projects\\cppSAT\\pySat\\SAT_problems\\small2.cnf", so_file_name, rhs_type=10)
#myProblem = SAT("C:\\Projects\\cppSAT\\pySat\\SAT_problems\\benchmark20\\random3SATn20M85S2.cnf", so_file_name, rhs_type=10)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses


In [ ]:
wp = Warning_propagator(myProblem)
myProblem.set_G( wp.get_clause_graph() )
wp.plot_graph(myProblem.G)

In [ ]:
myProblem.G.nodes

In [ ]:
init_s = 2*np.random.rand(N) - np.ones(N)

In [ ]:
L = len(list(myProblem.G.edges))
init_baux = np.ones(L) + 9*np.random.rand(L)
init_baux[550] = 0.0
L

In [ ]:
#solver = CTD(myProblem, initial_s=init_s, initial_baux=init_baux)
solver = CTD(myProblem, initial_s=init_s, random_aux=True)
solver.fast_solve(t_max=25.0, solver_type='LSODA', exit_type=ORTANT)

In [ ]:
plot_traj_js(solver, False)

In [ ]:
t, s = solver.get_satisfied_C_of_t()
plot_C_of_t((t, [elem/M for elem in s]))

In [ ]:
plot_aux_js(solver, False, None)

In [ ]:
list(myProblem.G.edges)[529]

In [ ]:
myProblem.clauses[123]

In [ ]:
myProblem.clauses[162]

In [ ]:
generate_sym_heatmap_from_matrix(solver)

In [ ]:
memory_distribution_from_matrix(solver)

In [ ]:
cutoff = 1.0005
initial_baux = np.empty(M*M)
for idx, traj in enumerate(solver.sol.y):
    if idx >= N:
        i = idx-N
        if traj[-1] <= cutoff:
            initial_baux[i] = 0.0
        else:
            initial_baux[i] = 1.0

In [ ]:
solver_2 = CTD(myProblem, initial_s=init_s, initial_baux=initial_baux)
solver_2.fast_solve(t_max=1.0, solver_type='LSODA', exit_type=ORTANT)
plot_traj_js(solver_2, False)

In [ ]:
generate_sym_heatmap_video_from_matrices(solver)

In [ ]:
N = solver.problem.number_of_variables
M = solver.problem.number_of_clauses

#b_mn = np.ones(int(M*(M+1)/2))
#for idx, traj in enumerate(solver.sol.y):
#    if idx > N:
#        b_mn[idx-N-1] = traj[-1]

# Create an empty NxN matrix
matrix = np.zeros((M, M))

# Fill the upper triangle of the matrix using the input vector
index = 0
for m in range(M):
    for n in range(M):
        if n >= m:
            matrix[m][n] = b_mn[index]
            index += 1

a = M-1
b = M-1
print(matrix[a][b])
print(matrix[b][a])

## Run based on correlation matrices

In [1]:
from pySAT import SAT, CTD, ORTANT
import numpy as np


so_file_name = "c_libs/cSAT.so"
myProblem = SAT("SAT_problems\\SATLIB_Benchmark_problems_N50\\uf50-06.cnf", so_file_name, lmbd = 0.05, rhs_type=12)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses
init_s= 2*np.random.rand(N) - np.ones(N)

In [2]:
import numpy as np

def get_pairs_from_file(threshold = -0.07):

    def read_numpy_array_from_file(filename):
        try:
            # Read data from file
            data = np.loadtxt(filename)

            # Return the numpy array
            return data
        except FileNotFoundError:
            print("File not found. Please check the file path.")
            return None
        except Exception as e:
            print("An error occurred:", e)
            return None

    # Example usage:
    filename = "results\\Botond\\km2_uf50-06_correlation_matrix_100.txt"
    array_from_file = read_numpy_array_from_file(filename)

    Botonds_pairs = []

    for i in range(M):
        for j in range(M):
            if array_from_file[i, j] < threshold and i > j:
                Botonds_pairs.append((i, j))
            elif i == j:
                Botonds_pairs.append((i, j))

    return Botonds_pairs

In [3]:
myProblem.set_pairs(get_pairs_from_file())
print(len( get_pairs_from_file() ))

651


In [4]:
solver = CTD(myProblem, initial_s=init_s)
solver.fast_solve(t_max=25.0, solver_type='LSODA', exit_type=ORTANT)

In [28]:
plot_traj_js(solver)

In [29]:
plot_aux_js(solver)

## Memory supression with correlation

# Recurrence prevention

### Potential

$$
V\left(s, a \right) = \sum_{m=1}^M a_m K_m(s)^2 + \gamma \sum_{l=1}^{L(t)} \frac{1}{|s-s_l|}
$$

In [ ]:
from pySAT import SAT, CTD, RHS_TYPE_RECPREV, ORTANT, HYPER_SPHERE, RHS_TYPE_THREE
import numpy as np

so_file_name = 'c_libs/cSat.so'
myProblem = SAT('SAT_problems/benchmark_maxaux/random3SATn15M64S3.cnf', None, rhs_type=RHS_TYPE_RECPREV)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses

init_s =  2*np.random.rand(N) - np.ones(N)

solver = CTD(myProblem, initial_s=init_s, random_aux=False)
solver.fast_solve(t_max=250, solver_type='BDF', exit_type=ORTANT)


In [ ]:
plot_traj(solver.sol, myProblem.number_of_variables, True)
plot_aux(solver.sol, N, True)

In [ ]:
from pySAT import SAT, CTD, CONVERGENCE_RADIUS, HYPER_SPHERE, RHS_TYPE_POINTCHARGES, ORTANT
import numpy as np

so_file_name = 'c_libs/cSat.so'
#myProblem = SAT('SAT_problems/random3SATn15a4.266666666666667.cnf', None, rhs_type=RHS_TYPE_POINTCHARGES)
myProblem = SAT('SAT_problems/random3SATn8a4.5.cnf', None, rhs_type=RHS_TYPE_POINTCHARGES)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses

init_s =  2*np.random.rand(N) - np.ones(N)

solver = CTD(myProblem, initial_s=init_s, random_aux=False)
solver.fast_solve(t_max=500, solver_type='BDF', exit_type=ORTANT)

plot_traj(solver.sol, myProblem.number_of_variables, True)
plot_aux(solver.sol, N, True)


In [ ]:
solver.get_satisfied_C_of_t()

## Solution planting


In [ ]:
from pySAT import SAT, CTD, ORTANT
import numpy as np

so_file_name = 'c_libs/cSat.so'

k = 4
myProblem = SAT(None, so_file_name, 5, 2, planted=1, literal_number=k)
#print(myProblem.clauses)

print("Planted solution: ")
print(myProblem.planted_solutions)
print("All solutions:")
print(myProblem.all_solutions())
print("Clauses")
print(myProblem.clauses)
print("Downconverted clauses:")
myProblem.downconvert_4_3()
print(myProblem.clauses)
print("Downconverted solutions:")
print(myProblem.all_solutions())


# N, M = myProblem.number_of_variables, myProblem.number_of_clauses
# init_s =  2*np.random.rand(N) - np.ones(N)

# solver = CTD(myProblem, initial_s=init_s, random_aux=False)
# solver.fast_solve(t_max=250, solver_type='BDF', exit_type=ORTANT)

# print("Max aux:{0}".format(max(solver.sol.y[N:,-1])))
# plot_traj(solver.sol, myProblem.number_of_variables, True)
# plot_aux(solver.sol, N, True)
# myProblem.write_problem_to_file("planted"+str(k))

In [ ]:
from cProfile import label
from pySAT import SAT, CTD, ORTANT
import numpy as np
import matplotlib.pyplot as plt

so_file_name = 'c_libs/cSat.so'

n_init = 4
k = 4
lines = []
myProblem = SAT(None, so_file_name, n_init, 4.25/(2-4.25), planted=1, literal_number=k)
print(myProblem.clauses)
print("N:{0}, M:{1}, k: 4".format(myProblem.number_of_variables, myProblem.number_of_clauses))
print("Planted solution: ")
print(myProblem.planted_solutions)
print("All solutions:")
print(myProblem.all_solutions())

myProblem.downconvert_4_3()

N, M = myProblem.number_of_variables, myProblem.number_of_clauses
print("new N {0}, new M {1}, new alpha {2}".format(N, M, M/N))
init_s =  2*np.random.rand(N) - np.ones(N)
init_s[0:n_init] = myProblem.planted_solutions[0]
# solver = CTD(myProblem, initial_s=init_s, random_aux=False)
# solver.fast_solve(t_max=500, solver_type='RK45', exit_type=ORTANT)

# plot_traj(solver.sol, myProblem.number_of_variables, True)
# plot_aux(solver.sol, N, True)


# Profiling

### Misc1

In [ ]:
import time
from pSAT import SAT, RK4, CTD
from matplotlib import pyplot as plt
import numpy as np
import cProfile

myProblem = SAT('chaotic_SAT/2random3SATn11c53.cnf')
mIntegrator = RK4()
solver = CTD(myProblem, mIntegrator, random_aux=True)
cProfile.run('solver.solve()', 'restats.dat')

In [ ]:
import time
from pySAT import SAT as oldSAT
from pySAT_new import SAT as newSAT
import numpy as np
import cProfile

so_file_name = 'c_libs/cSat.so'

myProblem1 = oldSAT('C:\Projects\cppSAT\pySat\SAT_problems\\random3SATn60a4.9.cnf', so_file_name, rhs_type=1)
myProblem2 = newSAT('C:\Projects\cppSAT\pySat\SAT_problems\\random3SATn60a4.9.cnf', so_file_name, rhs_type=1)

N, M = myProblem1.number_of_variables, myProblem1.number_of_clauses

init_s = 2*np.random.rand(N) - np.ones(N)
init_a = np.ones(M)
init_state = np.concatenate((init_s, init_a), axis = None)
print(myProblem1.rhs(0.0, init_state)-myProblem2.rhs_new(0.0, init_state))

def test1():
    for t in range(10000):
        state = myProblem1.rhs(0.0, np.concatenate((2*np.random.rand(N) - np.ones(N), np.ones(M)), axis = None))

def test2():
    for t in range(10000):
        state = myProblem2.rhs_new(0.0, np.concatenate((2*np.random.rand(N) - np.ones(N), np.ones(M)), axis = None))

In [ ]:
cProfile.run('test1()', 'restats.dat')
cProfile.run('test2()', 'restats2.dat')

In [ ]:
import pstats
from pstats import SortKey
p = pstats.Stats('restats.dat')
p.strip_dirs().sort_stats(-1).print_stats()

p2 = pstats.Stats('restats2.dat')
p2.strip_dirs().sort_stats(-1).print_stats()

In [ ]:
from ctypes import CDLL, POINTER, c_double, c_int
from pySAT import SAT, CTD, RHS_TYPE_THREE, RHS_TYPE_ONE, RHS_TYPE_TWO, ORTANT, CONVERGENCE_RADIUS, RHS_TYPE_FOUR
import numpy as np
import time

myProblem3 = SAT('C:\Projects\cppSAT\pySat\SAT_problems\\random3SATn20a4.35.cnf', None, rhs_type = RHS_TYPE_THREE)
cSAT_functions = CDLL('c_libs/cSAT2.so')
cSAT_functions.rhs5.restype = None
cSAT_functions.rhs3.restype = None
cSAT_functions.rhs1.restype = None
cSAT_functions.rhs2.restype = None
N, M = myProblem3.number_of_variables, myProblem3.number_of_clauses

clause_matrix = myProblem3.c.flatten().astype(np.int32) # c
clause_matrix_pointer = clause_matrix.ctypes.data_as(POINTER(c_int))

times1 = []
times2 = []
diffs = []

for i in range(10000):
    state = np.concatenate((2*np.random.rand(N)-np.ones(N), np.ones(M)))
    state = state.astype(np.double) # s & a
    state_pointer = state.ctypes.data_as(POINTER(c_double))

    result1 = np.empty(N + M)
    result1 = result1.astype(np.double) # s & a
    result1_pointer = result1.ctypes.data_as(POINTER(c_double))

    result2 = np.empty(N + M)
    result2 = result2.astype(np.double) # s & a
    result2_pointer = result2.ctypes.data_as(POINTER(c_double))

    t1 = time.time()
    cSAT_functions.rhs4(N, M, clause_matrix_pointer, state_pointer, result1_pointer)
    t2 = time.time()
    cSAT_functions.rhs5(N, M, clause_matrix_pointer, state_pointer, result2_pointer)
    t3 = time.time()

    times1.append(t2-t1)
    times2.append(t3-t2)
    diffs.append(np.linalg.norm(result1 -result2))
print('rhs4 average time: {0}'.format(sum(times1)))
print('rhs5 average time: {0}'.format(sum(times2)))
print('Average difference magnitude: {0}'.format(sum(diffs)/len(diffs)))


### Speed-up tests


In [ ]:
from pySAT import CTD, ORTANT, HYPER_SPHERE
from pySAT import SAT as SAT_old
from pySAT_new import SAT as SAT_new
import numpy as np

import time

so_file_name = 'c_libs/cSat.so'
#so_file_name = None
myProblem1 = SAT_old("C:\\Projects\\cppSAT\\pySat\\SAT_problems\\benchmark4.256\\random3SATn60M256.cnf", so_file_name, rhs_type=3)
myProblem2 = SAT_new("C:\\Projects\\cppSAT\\pySat\\SAT_problems\\benchmark4.256\\random3SATn60M256.cnf", so_file_name, rhs_type=3)
N, M = myProblem1.number_of_variables, myProblem1.number_of_clauses

init_s = 2*np.random.rand(N) - np.ones(N)

start = time.time()
solver1 = CTD(myProblem1, initial_s=init_s, random_aux=False, initial_aux=np.ones(M))
solver1.fast_solve(t_max=200, solver_type='RK45', exit_type=ORTANT)
end = time.time()
print("The old method took:")
print(end - start)

start = time.time()
solver2 = CTD(myProblem2, initial_s=init_s, random_aux=False, initial_aux=np.ones(M))
solver2.fast_solve(t_max=200, solver_type='RK45', exit_type=ORTANT)
end = time.time()
print("The new method took:")
print(end - start)


In [ ]:
plot_traj_js(solver1)

In [ ]:
plot_traj_js(solver2)

# Plotting

### Path scaling

In [ ]:
def parse_path_length_file(directory_path) -> list:
    import os
    results = []
    for filename in os.listdir(directory_path):
            f = os.path.join(directory_path, filename)
            if os.path.isfile(f):
                with open(f, 'r') as mf:
                    lines = mf.readlines()
                    for lidx, line in enumerate(lines):
                        if lidx > 1 and lidx % 2 == 1:
                            results.append(float(line.replace(' ', '')))
    return results

def averaging_filter(array, ratio = 100) -> list:
    result = []
    resolution = int(len(array)/ratio)
    for i in range(resolution):
        result.append(sum(path_lengths_N20[i:i+1])/resolution)
    
    return result

path_lengths_N20 =  parse_path_length_file("C:\\Projects\\cppSAT\\pySat\\results\\path_length\\N20")
path_lengths_N50 =  parse_path_length_file("C:\\Projects\\cppSAT\\pySat\\results\\path_length\\N50")



In [ ]:
print(len(path_lengths_N20))
init_s = 2*np.random.rand(N) - np.ones(N)

In [ ]:
import numpy as np

path_lengths_N20.sort(reverse=False)
y = np.zeros(len(path_lengths_N20))
for idx, elem in enumerate(path_lengths_N20):
    if idx == 0:
        y[idx] = len(path_lengths_N20)
    else:
        y[idx] = y[idx-1] -1
#Selective prooning
y_vals = []
x_vals = np.array(path_lengths_N20[::2])


In [ ]:
import plotly.graph_objs as go

# Define the x and y values
#x_vals = [1, 2, 3, 4, 5]
#y_vals = [0.2, 0.4, 0.1, 0.3, 0.5]

# Define the horizontal and vertical lines for the plot
h_lines = []
v_lines = []

line_width = 1 # set the line width here

for i in range(len(x_vals)-1):
    h_lines.append(go.Scatter(x=[x_vals[i], x_vals[i+1]], y=[y_vals[i], y_vals[i]], mode='lines', line=dict(width=line_width, color='blue'), showlegend=False))
    v_lines.append(go.Scatter(x=[x_vals[i+1], x_vals[i+1]], y=[y_vals[i], y_vals[i+1]], mode='lines', line=dict(width=line_width, color='blue'), showlegend=False))

# Create the plot
fig = go.Figure(data=h_lines + v_lines)

# Set the layout
fig.update_layout(title='Variable Width Bar Graph',
                  xaxis_title='X-Axis',
                  yaxis_title='Y-Axis',
                  yaxis_type='log',
                  legend=dict(
                      orientation="h",
                      yanchor="bottom",
                      y=1.02,
                      xanchor="right",
                      x=1
                  ))

# Display the plot
fig.show()


### idk

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

xs = list(range(2,9))
max_times = [113.39839488107091, 103.37222177560218, 122.75091766121237, 141.63069004410957, 196.16664532045627, 196.10582694555114, 236.87833199484706]
plt.grid(True)
plt.xlabel('Logarithm of resolution of basin boundary image')
plt.plot(xs, max_times, 'b+', label='times')
plt.plot(xs, max_times, 'y--', label='times')
plt.ylabel('Analog time to solve longest initial condition')
plt.show()



In [ ]:
import numpy as np
import matplotlib.pyplot as plt

xs = list(range(3,9))
bbes = [0.5929533174474745, 0.7917564981137991, 0.5645170148274746, 0.5202423186763236, 0.5331399348383494, 0.5094889272364818]
plt.grid(True)
plt.xlabel('Logarithm of resolution of basin boundary image')
plt.plot(xs, bbes, label='entropies')
plt.ylabel('Basin boundary entropy of the image')
plt.legend()
plt.show()

In [ ]:
# import required module
import os
import numpy as np
 
# assign directory
directory = 'results\\p'
directory2 = 'results\\p2'
directory3 = 'results\\p3'
 
# Variables to write data in
samesol = np.zeros(20)
diffsol = np.zeros(20)
samesol2 = np.zeros(20)
diffsol2 = np.zeros(20)
samesol3 = np.zeros(20)
diffsol3 = np.zeros(20)

# iterate over files in
# that directory
for filename in os.scandir(directory):
    if filename.is_file():
        with open(filename, 'r') as mahFile:
            lines = mahFile.readlines()
            for idx, line in enumerate(lines):
                if idx > 3:
                    if (int(line) > 0):
                        samesol[idx-4] += 1
                    else:
                        diffsol[idx-4] += 1

ps_n50 = [s/(s+d) for(s, d) in zip (samesol, diffsol)]
#print(ps_n50)

for filename in os.scandir(directory2):
    if filename.is_file():
        with open(filename, 'r') as mahFile:
            lines = mahFile.readlines()
            for idx, line in enumerate(lines):
                if idx > 3:
                    if (int(line) > 0):
                        samesol2[idx-4] += 1
                    else:
                        diffsol2[idx-4] += 1

ps_n45 = [s/(s+d) for(s, d) in zip (samesol2, diffsol2)]

for filename in os.scandir(directory3):
    if filename.is_file():
        with open(filename, 'r') as mahFile:
            lines = mahFile.readlines()
            for idx, line in enumerate(lines):
                if idx > 3:
                    if (int(line) > 0):
                        samesol3[idx-4] += 1
                    else:
                        diffsol3[idx-4] += 1

ps_n60 = [s/(s+d) for(s, d) in zip (samesol3, diffsol3)]

### Separation 

In [ ]:
import matplotlib.pyplot as plt
import numpy as np

dos_n15 = [1.00000000e-16, 6.15848211e-16, 3.79269019e-15, 2.33572147e-14
, 1.43844989e-13, 8.85866790e-13, 5.45559478e-12, 3.35981829e-11
, 2.06913808e-10, 1.27427499e-09, 7.84759970e-09, 4.83293024e-08
, 2.97635144e-07, 1.83298071e-06, 1.12883789e-05, 6.95192796e-05
, 4.28133240e-04, 2.63665090e-03, 1.62377674e-02, 1.00000000e-01]
ps_n15 = [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0
, 1.0, 1.0, 1.0, 0.998, 1.0, 0.994, 0.978, 0.888]

dos_n30 = [1.00000000e-14, 4.83293024e-14, 2.33572147e-13, 1.12883789e-12
, 5.45559478e-12, 2.63665090e-11, 1.27427499e-10, 6.15848211e-10
, 2.97635144e-09, 1.43844989e-08, 6.95192796e-08, 3.35981829e-07
, 1.62377674e-06, 7.84759970e-06, 3.79269019e-05, 1.83298071e-04
, 8.85866790e-04, 4.28133240e-03, 2.06913808e-02, 1.00000000e-01]
ps_n30 = [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.998
, 1.0, 1.0, 1.0, 0.998, 0.978, 0.968, 0.904, 0.782]

dos_n40 = [1.00000000e-14, 4.83293024e-14, 2.33572147e-13, 1.12883789e-12
, 5.45559478e-12, 2.63665090e-11, 1.27427499e-10, 6.15848211e-10
, 2.97635144e-09, 1.43844989e-08, 6.95192796e-08, 3.35981829e-07
, 1.62377674e-06, 7.84759970e-06, 3.79269019e-05, 1.83298071e-04
, 8.85866790e-04, 4.28133240e-03, 2.06913808e-02, 1.00000000e-01]
ps_n40 = [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.995
, 1.0, 1.0, 1.0, 0.99, 0.96,0.96, 0.885, 0.745]

dos_n50 = np.logspace(-14, -1, 20, endpoint=True, base=10)
dos_n45 = np.logspace(-14, -1, 20, endpoint=True, base=10)
dos_n60 = np.logspace(-14, -1, 20, endpoint=True, base=10)

with plt.style.context('ggplot'):#'seaborn-darkgrid'):
    #plt.grid(True)
    plt.xscale("log")
    plt.xlabel("Initial condition separation ($\delta_0$)")
    plt.ylabel("Trajectories corresponding to same solution")
    plt.plot(dos_n15, ps_n15, label='n=15')
    plt.plot(dos_n30, ps_n30, label='n=30')
    plt.plot(dos_n40, ps_n40, label='n=40')
    plt.plot(dos_n45, ps_n45, label='n=45')
    plt.plot(dos_n50, ps_n50, label='n=50')
    #plt.plot(dos_n60, ps_n60, label='n=60')
    plt.legend()
    #plt.show()
    plt.savefig("p_plot.png", dpi=350)

In [ ]:
# import required module
import os
 
# assign directory
directory = 'results\\time_to_solution'
directory2 = 'results\\time_to_solution2'
 
# List to write data in
times_to_solutions = []
times_to_solutions2 = []

# iterate over files in
# that directory
for filename in os.scandir(directory):
    if filename.is_file():
        with open(filename, 'r') as mahFile:
            lines = mahFile.readlines()
            for idx, line in enumerate(lines):
                if idx > 2:
                    times_to_solutions.append(float(line))

for filename in os.scandir(directory2):
    if filename.is_file():
        with open(filename, 'r') as mahFile:
            lines = mahFile.readlines()
            for idx, line in enumerate(lines):
                if idx > 2:
                    times_to_solutions2.append(float(line))

In [ ]:
import numpy as np
xs = np.linspace(0.0, max(times_to_solutions), 100)
ys = [sum(i > x for i in times_to_solutions) for x in xs]
ys = [y/max(ys) for y in ys]
xs2 = np.linspace(0.0, max(times_to_solutions2), 100)
ys2 = [sum(i > x for i in times_to_solutions2) for x in xs]
ys2 = [y/max(ys) for y in ys]


In [ ]:
xsa = [ x for (x, y) in zip(xs, ys) if x >= 240 and x <= 440]
ysa = [ y for (x, y) in zip(xs, ys) if x >= 240 and x <= 440]
coeffs = np.polyfit(xsa, np.log(ysa), 1, w=np.sqrt(ysa))
xsb = [ x for (x, y) in zip(xs2, ys2) if x >= 240 and x <= 400]
ysb = [ y for (x, y) in zip(xs2, ys2) if x >= 240 and x <= 400]
coeffs2 = np.polyfit(xsb, np.log(ysb), 1, w=np.sqrt(ysb))
print(coeffs)
print(coeffs2)

In [ ]:
import matplotlib.pyplot as plt

plt.grid(True)
plt.xlabel("Analog time")
plt.ylabel("Fraction of trajectories")
plt.yscale("log")
plt.plot(xs, ys, label="measured n=50")
plt.plot(xs2, ys2, label="measured n=20")
A = "{0:.3f}".format(coeffs[1])
B = "{0:.3f}".format(coeffs[0])
C = "{0:.3f}".format(coeffs2[1])
D = "{0:.3f}".format(coeffs2[0])
plt.plot([x for x in xs if x > 220 and x < 400], [1.4*np.exp(coeffs[1]) * np.exp(coeffs[0] * x) for x in xs if x > 220 and x < 400], label="p1(t)= {0}*exp({1}t)".format(A, B))
plt.plot([x for x in xs2 if x > 220 and x < 400], [0.7*np.exp(coeffs2[1]) * np.exp(coeffs2[0] * x) for x in xs2 if x > 220 and x < 400], label="p2(t)= {0}*exp({1}t)".format(C, D))
plt.legend()
plt.savefig('escape_times_with_kappa.png', dpi=350)

### $\kappa$ vs max(aux)

In [ ]:
import os
import numpy as np
 
# assign directory
directory = 'results\\kappaux'
 
# Lists to write data in
kappas = []
average_maxauxs = []


# iterate over files in
# that directory
for fidx, filename in enumerate(os.scandir(directory)):
    if filename.is_file():
        with open(filename, 'r') as mahFile:
            escape_times = np.zeros(200)
            max_auxs = np.zeros(200)
            lines = mahFile.readlines()
            for line in lines:
                if line[:3] =="idx":
                    idx = int(line.split(' ')[0].split("idx")[1][:-1])
                    if "kappa" in line:
                        escape_times[idx] = float(line.split(',')[1].replace(' ', '').replace(')', ''))
                        #escape_times[idx] = float(line.split('(')[1].split(',')[0])
                    if "maxAux" in line:
                        max_auxs[idx] = float(line.split('(')[1].split(',')[0])
            #Calculating kappa
            xs = np.linspace(0.0, max(escape_times), 99)
            ys = [sum(i > x for i in escape_times) for x in xs][:-1]
            #ys = [y/max(ys) for y in ys]
            xs = xs[:-1]
            coeffs = np.polyfit(xs, np.log(ys), 1, w=np.sqrt(ys))
            kappas.append(-coeffs[0])
            #Calculating average maxAux
            average_maxauxs.append(sum(max_auxs)/len(max_auxs))
            



In [ ]:
import matplotlib.pyplot as plt

#coeffs = np.polyfit(kappas, np.log(average_maxauxs), 1, w=np.sqrt(average_maxauxs))
coeffs2 = np.polyfit(kappas, np.reciprocal(average_maxauxs), 1, w=np.sqrt(average_maxauxs))
#print(len(kappas))
#print(len(average_maxauxs))
with plt.style.context('ggplot'):
    plt.xlabel("Escape rate ($\kappa$)")
    plt.ylabel("Maximum aux untill solution")
    plt.yscale("log")
    plt.xscale("log")
    plt.plot(kappas, average_maxauxs, '+', label='Simulation data (first escape $r=\sqrt{N} \cdot 0.95$)')
    #mahx, mahy = zip(*sorted(zip(kappas, [np.exp(coeffs[1]) * np.exp(coeffs[0] * x) for x in kappas])))
    mahx2, mahy2 = zip(*sorted(zip(kappas, [1/(coeffs2[1] + coeffs2[0] * x) for x in kappas])))
    #plt.plot(mahx, mahy, label="Fitted exponential curve")
    plt.plot(mahx2, mahy2, label="Fitted harmonic curve")
    plt.legend()
    print("maxAux = 1/({0}*kappa + {1})".format(coeffs2[0], coeffs2[1]))
    plt.savefig('kappa_maxaux.png', dpi=350)

In [ ]:
import os
import numpy as np
 
# assign directory
directory = 'results\\exp_mem\\N15'
 
# Lists to write data in
trajs = []
# x axis data
lambdas = np.logspace(-5, 0.0, num=20)-0.00001

# iterate over files in
# that directory
for fidx, filename in enumerate(os.scandir(directory)):
    
    if filename.is_file():
        with open(filename, 'r') as mahFile:
            one_traj = []
            lines = mahFile.readlines()
            for idx, line in enumerate(lines):
                if idx > 1:
                    elements = [i for i in line.split(" ") if i]
                    for element in elements:
                        dummy = element.replace('[', '')
                        dummy = dummy.replace(']', '')
                        dummy = dummy.replace('\n', '')
                        try:
                            one_traj.append(float(dummy))
                        except Exception as err:
                            pass
            trajs.append(one_traj)

print([len(i) for i in trajs])

### Memory supression

In [ ]:
import matplotlib.pyplot as plt

with plt.style.context('ggplot'):
    plt.xlabel("Escape rate ($\lambda$)")
    plt.ylabel("Time untill solution")
    plt.xscale("log")
    plt.scatter(lambdas, trajs[2])


In [ ]:
# x and y given as DataFrame columns
import plotly.graph_objects as go

fig = go.Figure()

for idx, traj in enumerate(trajs):
    fig.add_trace(go.Scatter(x=lambdas, y=traj, name=str(idx), mode='lines+markers'))

fig.update_xaxes(title_text=u"\u03BB", type="log")
#fig.add_scatter(x=lambdas, y=trajs[2], log_x=True)
fig.show()

## Baux stat

In [13]:
succes_plot_data = {}

In [24]:
import os
from pySAT import SAT, CTD

# Define dictionaries to store the processed data for each type
data_amkm2 = {}
data_CG = {}
data_RG = {}
data_amkm = {}

def extract_info(filename):
    parts = filename.split('_')
    problem_name = parts[0]
    initial_condition_index = int(parts[1][3:])
    type_name = parts[2].split('.')[0]  # Remove the file extension
    if type_name not in ["amkm2", "CG", "RG", "amkm"]:
        raise ValueError("Invalid type name")
    return problem_name, initial_condition_index, type_name

N = 100
# Iterate through files in the library
library_path = "results\\Baux_stat\\N{0}".format(N)
problem_folder = "SAT_problems\\SATLIB_Benchmark_problems_N{0}".format(N)
for filename in os.listdir(library_path):
    if filename.endswith(".sol"):
        problem_name, initial_condition_index, type_name = extract_info(filename)
        my_rhs_type = None
        so_file_name = "c_libs/cSAT.so"
        myProblem = SAT(os.path.join(problem_folder, problem_name), so_file_name)
        N, M = myProblem.number_of_variables, myProblem.number_of_clauses
        solver = None


        # Update the corresponding data dictionary based on type
        if type_name == "amkm2":
            if problem_name not in data_amkm2:
                data_amkm2[problem_name] = {}
            
            my_rhs_type = 3
            myProblem = SAT(os.path.join(problem_folder, problem_name), so_file_name, rhs_type=my_rhs_type)
            try:
                solver = CTD.load_sol_from_file(os.path.join(library_path, filename), myProblem)
                data_amkm2[problem_name][initial_condition_index] = solver
            except Exception as err:
                print(problem_name + type_name + str(initial_condition_index))
        
        elif type_name == "CG":
            if problem_name not in data_CG:
                data_CG[problem_name] = {}
            
            my_rhs_type = 12
            myProblem = SAT(os.path.join(problem_folder, problem_name), so_file_name, rhs_type=my_rhs_type)
            try:
                solver = CTD.load_sol_from_file(os.path.join(library_path, filename), myProblem)
                data_CG[problem_name][initial_condition_index] = solver
            except Exception as err:
                print(problem_name + type_name + str(initial_condition_index))
        
        elif type_name == "RG":
            if problem_name not in data_RG:
                data_RG[problem_name] = {}
            my_rhs_type = 12
            myProblem = SAT(os.path.join(problem_folder, problem_name), so_file_name, rhs_type=my_rhs_type)
            try:
                solver = CTD.load_sol_from_file(os.path.join(library_path, filename), myProblem)
                data_RG[problem_name][initial_condition_index] = solver
            except Exception as err:
                print(problem_name + type_name + str(initial_condition_index))
        elif type_name == "amkm":
            if problem_name not in data_amkm:
                data_amkm[problem_name] = {}
            my_rhs_type = 1
            try:
                solver = CTD.load_sol_from_file(os.path.join(library_path, filename), myProblem)
                data_amkm[problem_name][initial_condition_index] = solver
            except Exception as err:
                print(problem_name + type_name + str(initial_condition_index))


In [25]:
succes_ps = [0.0, 0.0, 0.0, 0.0]
succes_p_labels = ["amkm2", "CG", "RG", "amkm"]
data_holder = [data_amkm2, data_CG, data_RG, data_amkm]
for d_idx, data_dict in enumerate(data_holder):
    run_nbr = 0
    for problem_idx, problem_name in enumerate(data_dict):
        for key, val in data_dict[problem_name].items():
            run_nbr += 1
            N = val.problem.number_of_variables
            if val.problem.check_solution([True if elem > 0 else False for elem in val.sol.y[:N,-1]]):
                succes_ps[d_idx] += 1
    if run_nbr == 0:
        run_nbr = 1
    succes_ps[d_idx] = succes_ps[d_idx] / run_nbr
succes_plot_data[N] = succes_ps


In [27]:
print(succes_p_labels)
succes_plot_data

['amkm2', 'CG', 'RG', 'amkm']


{20: [0.9, 0.4, 0.6, 1.0],
 50: [0.3, 0.3333333333333333, 0.1, 0.7],
 75: [0.0, 0.0, 0.1, 0.6],
 100: [0.11764705882352941, 0.0, 0.0, 0.3333333333333333]}

# Factor - graph

In [ ]:
from pySAT import SAT, CTD, ORTANT, Warning_propagator, BIPARTITE_PLOT, SPRING_PLOT
import numpy as np

so_file_name = 'c_libs/cSat.so'
#myProblem = SAT('SAT_problems/Benchmark_problems_N20/uf20-01.cnf', so_file_name, rhs_type=10, lmbd=0.4)
myProblem = SAT('SAT_problems/easy.cnf', so_file_name, rhs_type=1, lmbd=0.4)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses

In [ ]:
seed = 2214

wp = Warning_propagator(myProblem)
wp.plot_factorgraph(BIPARTITE_PLOT, seed, SHIFT_CLAUSE_LABEL = False)

In [ ]:
import networkx as nx
from itertools import combinations

def all_pairs(iterable):
    # Generate all combinations of length 2 from the iterable
    for pair in combinations(iterable, 2):
        # Yield the pair if the first element is smaller than the second
        if pair[0] < pair[1]:
            yield pair

#Making a copy of the factor graph
G = wp.g.copy()

variable_nodes = [node for node, data in G.nodes(data=True) if data.get('type') == 'variable']
for node in variable_nodes:
    neighbours = list(G.neighbors(node))
    edge_signs = [G[node][neighbour]['weight'] for neighbour in neighbours]

    print("Neighbours of variable {0} are: {1} with colours {2}".format(node+1, [x+1 for x in neighbours], edge_signs))
    for u, v in all_pairs(neighbours):

        print("u:{0}  v:{1}, with weight summ {2}".format(u+1, v+1, edge_signs[neighbours.index(u)] + edge_signs[neighbours.index(v)]))
    #for neighbour in neighbours:
    #    weight = G[node][neighbour]['weight']

In [ ]:
clause_graph = wp.get_clause_graph()
wp.plot_graph(clause_graph, N, seed)

In [ ]:
#wp.get_k_core_graph(clause_graph, 2).nodes
wp.plot_graph(wp.get_k_core_graph(clause_graph, 3), N, seed)

In [ ]:
import os
from pySAT import SAT, CTD, ORTANT, Warning_propagator, BIPARTITE_PLOT, SPRING_PLOT
import numpy as np

problem_directory = "SAT_problems/Benchmark_problems_N100/"
so_file_name = 'c_libs/cSat.so'
kcore = 4
xs = []
ys = []

for filename in os.listdir(problem_directory):
    f = os.path.join(problem_directory, filename)
    myProblem = SAT(f, so_file_name, rhs_type=10, lmbd=0.4)
    N, M = myProblem.number_of_variables, myProblem.number_of_clauses
    wp = Warning_propagator(myProblem)
    xs.append(len(wp.get_clause_graph().edges()))
    ys.append(len(wp.get_k_core_edges(kcore)))

norm = max(xs)
xs = [x / norm for x in xs]
ys = [y / norm for y in ys]

In [ ]:
problem_directory = "SAT_problems/Benchmark_problems_N20/"
so_file_name = 'c_libs/cSat.so'
kcore = 4
xs2 = []
ys2 = []

for filename in os.listdir(problem_directory):
    f = os.path.join(problem_directory, filename)
    myProblem = SAT(f, so_file_name, rhs_type=10, lmbd=0.4)
    N, M = myProblem.number_of_variables, myProblem.number_of_clauses
    wp = Warning_propagator(myProblem)
    xs2.append(len(wp.get_clause_graph().edges()))
    ys2.append(len(wp.get_k_core_edges(kcore)))

norm = max(xs2)
xs2 = [x / norm for x in xs2]
ys2 = [y / norm for y in ys2]

In [ ]:
problem_directory = "SAT_problems/Benchmark_problems_N75/"
so_file_name = 'c_libs/cSat.so'
kcore = 4
xs3 = []
ys3 = []

for filename in os.listdir(problem_directory):
    f = os.path.join(problem_directory, filename)
    myProblem = SAT(f, so_file_name, rhs_type=10, lmbd=0.4)
    N, M = myProblem.number_of_variables, myProblem.number_of_clauses
    wp = Warning_propagator(myProblem)
    xs3.append(len(wp.get_clause_graph().edges()))
    ys3.append(len(wp.get_k_core_edges(kcore)))

norm = max(xs3)
xs3 = [x / norm for x in xs3]
ys3 = [y / norm for y in ys3]

In [ ]:
problem_directory = "SAT_problems/5SAT/"
so_file_name = 'c_libs/cSat.so'
kcore = 4
xs4 = []
ys4 = []

for filename in os.listdir(problem_directory):
    f = os.path.join(problem_directory, filename)
    myProblem = SAT(f, so_file_name, rhs_type=10, lmbd=0.4)
    N, M = myProblem.number_of_variables, myProblem.number_of_clauses
    wp = Warning_propagator(myProblem)
    xs4.append(len(wp.get_clause_graph().edges()))
    ys4.append(len(wp.get_k_core_edges(kcore)))

norm = max(xs4)
xs4 = [x / norm for x in xs4]
ys4 = [y / norm for y in ys4]

In [ ]:
import plotly.graph_objs as go

# Scatter plot
scatter_trace = go.Scatter(
    x=xs,
    y=ys,
    mode='markers',
    marker=dict(
        size=10,
        color='blue',  # you can change the color if you like
        opacity=0.8,
    ),
    name='N=100 3SAT problems'
)

scatter_trace2 = go.Scatter(
    x=xs2,
    y=ys2,
    mode='markers',
    marker=dict(
        size=10,
        color='red',  # you can change the color if you like
        opacity=0.8,
    ),
    name='N=20 3SAT problems'
)

scatter_trace3 = go.Scatter(
    x=xs3,
    y=ys3,
    mode='markers',
    marker=dict(
        size=10,
        color='green',  # you can change the color if you like
        opacity=0.8,
    ),
    name='N=75 3SAT problems'
)

scatter_trace4 = go.Scatter(
    x=xs4,
    y=ys4,
    mode='markers',
    marker=dict(
        size=10,
        color='black',  # you can change the color if you like
        opacity=0.8,
    ),
    name='N=250 5SAT problems'
)


# Layout
layout = go.Layout(
    title='Random k-SAT Problems',
    xaxis=dict(title='Normalized number of edges of clause graphs'),
    yaxis=dict(title='Normalized number of edges of {0}-core graphs'.format(kcore))
)

# Combine traces
fig = go.Figure(data=[scatter_trace, scatter_trace2, scatter_trace3, scatter_trace4], layout=layout)

# Plot
fig.show()


# HOM 2

## Pruning 1

In [ ]:
import re
import plotly.graph_objects as go

# Read the text file
with open('C:\\Projects\\cppSAT\\pySat\\results\\HOM\\naive_pruning\\second_order_mem_prune_N15.o685886.1', 'r') as file:
    data = file.read()

with open('C:\\Projects\\cppSAT\\pySat\\results\\HOM\\naive_pruning\\second_order_mem_prune_N15.o685886.3', 'r') as file:
    data2 = file.read()

# Extract numbers using regular expressions
prunes = re.findall(r"Prune: (\d+)%", data)
times = re.findall(r"Final time:\n([\d.]+)", data)

prunes2 = re.findall(r"Prune: (\d+)%", data2)
times2 = re.findall(r"Final time:\n([\d.]+)", data2)

# Convert extracted numbers to float
prunes = [int(prune) for prune in prunes]
times = [float(time) for time in times]

prunes2 = [int(prune) for prune in prunes2]
times2 = [float(time) for time in times2]

# Sort the lists based on prunes
prunes, times = zip(*sorted(zip(prunes, times)))

prunes2, times2 = zip(*sorted(zip(prunes2, times2)))


# Create the plot
fig = go.Figure()
fig.add_trace(go.Scatter(x=prunes, y=times, mode='markers+lines'))

fig.add_trace(go.Scatter(x=prunes2, y=times2, mode='markers+lines'))

# Set plot title and axes labels
fig.update_layout(
    title="Final Time vs Prune Percentage",
    xaxis_title="Prune Percentage",
    yaxis_title="Final Time"
)

fig.show()

In [ ]:
import plotly.graph_objects as go
import numpy as np

y1 = np.array([61, 55, 60, 55, 40]) + np.ones(5)
y1 = y1 + 1.5*(2*np.random.rand(5) - np.ones(5))
y2 = 0.7* y1 + 10*(2*np.random.rand(5) - np.ones(5)) -1.5*np.array([i for i in range(5)])
ns = [10 , 15, 20, 25, 30]

# Create the plot
fig = go.Figure()
fig.add_trace(go.Scatter(x=ns, y=y1, mode='markers+lines', name="With OPO potential"))
fig.add_trace(go.Scatter(x=ns, y=y2, mode='markers+lines', name="Without OPO potential"))


# Set plot title and axes labels
fig.update_layout(
    title="Final Time vs Prune Percentage",
    xaxis_title="Problem size",
    yaxis_title="Succes probability",
    legend=dict(x=0.15, y=0.15)  # Move legends inside the plot area
)

fig.show(layout=layout)

In [ ]:
import numpy as np
2*np.random.rand(5) - np.ones(5)

In [ ]:
import os
import re
import plotly.graph_objects as go

# Get a list of all files in the 'data' folder
data_folder = 'C:\\Projects\\cppSAT\\pySat\\results\\HOM\\plot_data'
files = os.listdir(data_folder)

# Initialize lists to store data
all_prunes = []
all_times = []

# Iterate through each file in the 'data' folder
for file_name in files:
    # Read the text file
    with open(os.path.join(data_folder, file_name), 'r') as file:
        data = file.read()

    # Extract numbers using regular expressions
    prunes = re.findall(r"Prune: (\d+)%", data)
    times = re.findall(r"Relative final time:\n([\d.]+)", data)

    # Convert extracted numbers to float
    prunes = [int(prune) for prune in prunes]
    times = [float(time) for time in times]

    # Sort the lists based on prunes
    prunes, times = zip(*sorted(zip(prunes, times)))

    # Append the data to the lists
    all_prunes.append(prunes)
    all_times.append(times)

# Create the plot
fig = go.Figure()

# Iterate through each set of data
for i in range(len(files)):
    # Add scatter plot for each data set
    fig.add_trace(go.Scatter(x=all_prunes[i], y=all_times[i], mode='markers+lines', name='Data {}'.format(i+1)))

# Set plot title and axes labels
fig.update_layout(
    title="Final Time vs Prune Percentage",
    xaxis_title="Prune Percentage",
    yaxis_title="Final Time/Base time"
)

fig.show()

In [ ]:
def parse_maxaux_file(filename):
    list1 = []
    list2 = []

    with open(filename, 'r') as file:
        lines = file.readlines()

    for i in range(0, len(lines), 3):
        line = lines[i].strip()
        rhs_type_line = lines[i+1].strip()
        maxaux_line = lines[i+2].strip()
        
        if rhs_type_line == "rhs_type:3":
            max_aux_value = float(maxaux_line.split("max_aux:")[1])
            n_value = int(line.split("N")[1].split("M")[0])
            list1.append((max_aux_value, n_value))
        else:
            max_aux_value = float(maxaux_line.split("max_aux:")[1])
            n_value = int(line.split("N")[1].split("M")[0])
            list2.append((max_aux_value, n_value))

    return list1, list2

def parse_maxaux_file_2(filename, init_array=None):
    if not init_array:
        results = []
    else:
        results = [elem for elem in init_array]

    with open(filename, 'r') as file:
        lines = file.readlines()

    for i in range(0, len(lines), 6):
        line_1 = lines[i].strip()
        rhs_type_line_1 = lines[i+1].strip()
        maxaux_line_1 = lines[i+2].strip()

        line_2 = lines[i+3].strip()
        rhs_type_line_2 = lines[i+4].strip()
        maxaux_line_2 = lines[i+5].strip()
        
        if rhs_type_line_1 == "rhs_type:3":
            max_aux_value = float(maxaux_line_1.split("max_aux:")[1])
            n_value_1 = int(line_1.split("N")[1].split("M")[0])

        
            max_bau_value = float(maxaux_line_2.split("max_aux:")[1])
            n_value_2 = int(line_2.split("N")[1].split("M")[0])
            if n_value_1 == n_value_2:
                results.append((n_value_1, (max_aux_value-1)/(max_bau_value-1)))
            else:
                raise ValueError('ooh')

        else:
            raise ValueError('Ajjaj')

    return results



#a, b = parse_maxaux_file("results/bauxmax/max_aux_bmn_N10-20.o690724.2")
list_to_plot = parse_maxaux_file_2("results/bauxmax/max_aux_bmn_N10-20.o690724.2")
list_to_plot = parse_maxaux_file_2("results/bauxmax/max_aux_bmn_N10-20.o690724.1", list_to_plot)
list_to_plot = parse_maxaux_file_2("results/bauxmax/max_aux_bmn_N10-20.o690610.1", list_to_plot)



In [ ]:
def plot_bauxmax_points(list1, list2):
    import plotly.graph_objects as go
    import numpy as np

    x1 = [tup[1] for tup in list1]  # Extracting 'N' values from list1
    y1 = [tup[0] for tup in list1]  # Extracting max_aux values from list1

    x2 = [tup[1] for tup in list2]  # Extracting 'N' values from list2
    y2 = [tup[0] for tup in list2]  # Extracting max_aux values from list2

    # Calculate the average y value for each x value
    x1_avg = list(set(x1))
    y1_avg = [np.mean([y1[i] for i, x in enumerate(x1) if x == val]) for val in x1_avg]
    
    x2_avg = list(set(x2))
    y2_avg = [np.mean([y2[i] for i, x in enumerate(x2) if x == val]) for val in x2_avg]

    trace1 = go.Scatter(
        x=x1,
        y=y1,
        mode='markers',
        name='Original CTDS',
        marker=dict(
            color='blue',
            symbol='circle',
            size=8
        )
    )

    trace2 = go.Scatter(
        x=x2,
        y=y2,
        mode='markers',
        name='Clause correlation method',
        marker=dict(
            color='red',
            symbol='square',
            size=8
        )
    )

    trace1_avg = go.Scatter(
        x=x1_avg,
        y=y1_avg,
        mode='lines',
        name='Original CTDS (Average)',
        line=dict(
            color='blue',
            dash='dash'
        )
    )

    trace2_avg = go.Scatter(
        x=x2_avg,
        y=y2_avg,
        mode='lines',
        name='Clause correlation method (Average)',
        line=dict(
            color='red',
            dash='dash'
        )
    )

    layout = go.Layout(
        title='CTDS and CC comparison',
        xaxis=dict(title='N', tickmode='linear', dtick=1),
        yaxis=dict(title='Maximum aux value', type='log'),
        showlegend=True,
        legend=dict(x=0.15, y=0.95)  # Move legends inside the plot area
    )



    fig = go.Figure(data=[trace1, trace2, trace1_avg, trace2_avg], layout=layout)
    fig.show()


plot_bauxmax_points(a, b)


In [ ]:
def plot_bauxmax_points_2(list1):
    import plotly.graph_objects as go
    import numpy as np

    y1 = [tup[1] for tup in list1]  # Extracting 'N' values from list1
    x1 = [tup[0] for tup in list1]  # Extracting max_aux values from list1

    # Calculate the average y value for each x value
    x1_avg = list(set(x1))
    y1_avg = [np.mean([y1[i] for i, x in enumerate(x1) if x == val]) for val in x1_avg]

    trace1 = go.Scatter(
        x=x1,
        y=y1,
        mode='markers',
        name='Max aux ratio',
        marker=dict(
            color='red',
            symbol='cross',
            size=8
        )
    )

    trace1_avg = go.Scatter(
        x=x1_avg,
        y=y1_avg,
        mode='lines',
        name='(Average)',
        line=dict(
            color='black',
            dash='dash'
        )
    )

    layout = go.Layout(
        title='CTDS and CC comparison',
        xaxis=dict(title='N', tickmode='linear', dtick=1),
        yaxis=dict(title='Aux reduction', type='log'),
        showlegend=True,
        legend=dict(x=0.15, y=0.95)  # Move legends inside the plot area
    )



    fig = go.Figure(data=[trace1, trace1_avg], layout=layout)
    fig.show()

plot_bauxmax_points_2(list_to_plot)

## Pruning 2 speedup

This function calculates a matrix Q that enables the efficient computation of the vector s using sparse encoding.

### Inputs:
- **B**: The matrix B with elements indexed by (m, n).
- **C**: The matrix C.
- **K**: The matrix K.
- **edges**: A list of tuples (n, m) indicating non-zero elements in B.

### Outputs:
- **Q**: The calculated matrix Q.

### Derivation:
We aim to compute the vector s using the formula:
$$ s_i = \sum_{m,n} b_{mn} (c_{mi} K_{mi} K_m + c_{ni} K_{ni} K_n) $$

### Sparse Encoding:
Given the sparse nature of B, denoted by the graph G, we can rewrite the formula as a matrix-vector multiplication:
$ s = Q \cdot \tilde{b} $

### Matrix Q Calculation:
Each element $ Q_{i,j} $ of Q is calculated as follows:
$$ Q_{i,j} = \sum_{(m,n) \in G} b_{mn} (c_{mi} K_{mj} K_m + c_{ni} K_{n,j} K_n) $$

### Algorithm:
1. Initialize an empty matrix $Q$ of appropriate size.
2. Iterate over the edges $(n, m)$ in $G$.
3. For each edge, iterate over the rows of $B$.
4. Calculate the contribution to $ Q_{i,j} $ and directly assign it.
5. Return the calculated matrix $Q$.


In [ ]:
from pySAT import SAT, CTD, ORTANT, Warning_propagator
import numpy as np


so_file_name = "c_libs/cSAT.so"
myProblem = SAT("SAT_problems\\SATLIB_Benchmark_problems_N50\\uf50-06.cnf", so_file_name, lmbd = 0.05, rhs_type=12)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses
#init_s = np.array([ 0.1438395 ,  0.34579224, -0.77615392, -0.81310226])


In [ ]:
#wp = Warning_propagator(myProblem)
#myProblem.set_G(wp.get_clause_graph())
init_s= 2*np.random.rand(N) - np.ones(N)

### Function Explanation: Generate Pairs from Matrix

Given a matrix $ c $ of size $ N \times M $, the function aims to generate a list of pairs $ (m, n) $ such that iterating through each pair of rows $ c_m $ and $ c_n $, the function saves $ (m, n) $ to the resulting list if the vector $ c_m \cdot c_n $ (element-wise multiplication) has any non-zero element, except in the case when it has exactly one element equal to $-1$.

The function can be represented formally as follows:

#### Inputs:
- $ c $: Matrix of size $ N \times M $

#### Output:
- List of pairs $ (m, n) $ satisfying the conditions mentioned.

#### Algorithm:
1. Initialize an empty list $ \text{pairs} $.
2. Iterate through each pair of rows $ (c_m, c_n) $ where $ m $ ranges from $ 1 $ to $ N $ and $ n $ ranges from $ 1 $ to $ N $.
3. Compute the element-wise multiplication of the vectors $ c_m $ and $ c_n $.
4. If the resulting vector has any non-zero element and does not have exactly one element equal to $-1$, append $ (m, n) $ to the list $ \text{pairs} $.
5. Return the list $ \text{pairs} $.


#### Example:
Consider a matrix $ c $ of size $ 3 \times 3 $:
$$
c = \begin{bmatrix}
1 & 0 & -1 \\
0 & 1 & 0 \\
0 & 0 & 1 \\
\end{bmatrix} 
$$

- The function will iterate through pairs of rows $ (c_1, c_2) $, $ (c_1, c_3) $, $ (c_2, c_3) $.
- For pair $ (c_1, c_2) $, $ c_1 \cdot c_2 = [0, 0, -1] $, which has one $-1$ element, so this pair is excluded.
- For pair $ (c_1, c_3) $, $ c_1 \cdot c_3 = [0, 0, -1] $, which has one $-1$ element, so this pair is excluded.
- For pair $ (c_2, c_3) $, $ c_2 \cdot c_3 = [0, 0, 0] $, which has no non-zero elements, so this pair is excluded.
- Thus, the resulting list of pairs will be empty.

This markdown explanation provides a formal representation of the function and its behavior.


In [ ]:
resulting_pairs = [(i, i) for i in range(M)]
for m, c_m in enumerate(myProblem.c):
    for n, c_n in enumerate(myProblem.c):
        if n > m:
            product = [a*b for a, b in zip(c_m, c_n)]
            if product.count(0) != len(product):  # Check if there are non-zero element
                if not( product.count(-1) and product.count(0) == len(product) -1 ): # Check if there is not only one -1 elemnt in product
                    resulting_pairs.append( (n, m) )
            elif np.random.random() < 0.1: # Add the pair anyway, with probability 10%
                resulting_pairs.append( (n, m) )

myProblem.set_pairs(resulting_pairs)

In [ ]:
L = len(list(myProblem.G.edges))
b = 0.01*np.ones(L)

solver = CTD(myProblem, initial_s=init_s, initial_baux=b)
solver.fast_solve(t_max=50.0, solver_type='RK45', exit_type=ORTANT)

In [ ]:
from pySAT import SAT, CTD, ORTANT, Warning_propagator
import numpy as np

so_file_name = "c_libs/cSAT.so"
myProblem2 = SAT("SAT_problems\\SATLIB_Benchmark_problems_N50\\uf50-06.cnf", so_file_name, rhs_type=3)
#myProblem2 = SAT("SAT_problems\\Sam's_problems\\N1000\\p0.cnf", so_file_name, rhs_type=3)
N, M = myProblem2.number_of_variables, myProblem2.number_of_clauses
init_s= 2*np.random.rand(N) - np.ones(N)

In [ ]:
solver = CTD(myProblem2, initial_s=init_s, initial_aux=1.0*np.ones(M))
solver.fast_solve(t_max=300.0, solver_type='LSODA', exit_type=ORTANT)

In [ ]:
plot_traj_js(solver, False)

In [ ]:
plot_aux_js(solver, False, LOG_YAXIS_FLAG=False)

In [ ]:
import copy
solver_copy = copy.copy(solver)
solver_copy.continue_solution(300)

In [ ]:
plot_traj_js(solver_copy, False)

In [ ]:
plot_aux_js(solver_copy, False, LOG_YAXIS_FLAG=False)

In [ ]:
t, s = solver.get_satisfied_C_of_t()
plot_C_of_t((t, [elem/M for elem in s]))

In [ ]:
def indices_above_threshold(arr, threshold):
    """Returns (aparently ordered) list of indeces of the elements larger than threshold x max
    Indices start from one!
    """
    max_val = np.max(arr)
    threshold_val = threshold * max_val
    above_threshold_indices = np.where(arr > threshold_val)
    #sorted_indices = np.argsort(arr[above_threshold_indices])[::-1]
    #return above_threshold_indices[sorted_indices]
    return [elem + 1 for elem in above_threshold_indices[0]]

trouble_clauses = indices_above_threshold(solver.sol.y[N:,-1], 0.5)
print(trouble_clauses)

In [ ]:
wp = Warning_propagator(myProblem2)
da_graph = wp.shift_node_indices(wp.get_clause_graph())
wp.plot_graph(da_graph, color_nodes=trouble_clauses)

In [ ]:
import networkx as nx

myProblem2 = SAT("SAT_problems\\Sam's_problems\\N1000\\p0.cnf", so_file_name, rhs_type=3)
wp = Warning_propagator(myProblem2)
my_graph = wp.get_clause_graph()

for node in my_graph.nodes:
    my_graph.remove_edge(node, node)

for i in range(4,20):
    print("{0} : {1}".format(i, (len(nx.k_core(my_graph, i).nodes))))

In [ ]:
import networkx as nx
import numpy as np
import matplotlib.pyplot as plt

G = my_graph

degree_sequence = sorted((d for n, d in G.degree()), reverse=True)
dmax = max(degree_sequence)

fig = plt.figure("Degree of a random graph", figsize=(8, 8))
# Create a gridspec for adding subplots of different sizes
axgrid = fig.add_gridspec(5, 4)

ax0 = fig.add_subplot(axgrid[0:3, :])
Gcc = G.subgraph(sorted(nx.connected_components(G), key=len, reverse=True)[0])
pos = nx.spring_layout(Gcc, seed=10396953)
nx.draw_networkx_nodes(Gcc, pos, ax=ax0, node_size=20)
nx.draw_networkx_edges(Gcc, pos, ax=ax0, alpha=0.4)
ax0.set_title("Connected components of G")
ax0.set_axis_off()

ax1 = fig.add_subplot(axgrid[3:, :2])
ax1.plot(degree_sequence, "b-", marker="o")
ax1.set_title("Degree Rank Plot")
ax1.set_ylabel("Degree")
ax1.set_xlabel("Rank")

ax2 = fig.add_subplot(axgrid[3:, 2:])
ax2.bar(*np.unique(degree_sequence, return_counts=True))
ax2.set_title("Degree histogram")
ax2.set_xlabel("Degree")
ax2.set_ylabel("# of Nodes")

fig.tight_layout()
plt.show()

In [ ]:
nx_graph = da_graph
to_be_removed = []
neighbours_set = set()
for node in trouble_clauses:
    for neigbour in nx_graph.neighbors(node):
        neighbours_set.add(neigbour)

for node in nx_graph.nodes:
    if node in trouble_clauses:
        nx_graph.nodes[node]['group'] = 2
        nx_graph.nodes[node]['label'] = str(node)  + ' : 2'
    else:
        if node in neighbours_set:
            nx_graph.nodes[node]['group'] = 3
            nx_graph.nodes[node]['label'] = str(node) + ' : 3'
        else:
            nx_graph.nodes[node]['group'] = 1
            nx_graph.nodes[node]['label'] = str(node)  + ' : 1'
            #to_be_removed.append(node)
    nx_graph.remove_edge(node, node)
nx_graph.remove_nodes_from(to_be_removed)


In [ ]:
from pyvis.network import Network
nt = Network('750', '1500')
# populates the nodes and edges data structures
nt.from_nx(nx_graph)


# Define JavaScript functions to show nodes based on their groups
js_code = """
<script type="text/javascript">
function showGroup(groupNumber) {
    var nodes = network.body.data.nodes.get();
    for (var i = 0; i < nodes.length; i++) {
        if (nodes[i].group == groupNumber) {
            nodes[i].hidden = false;
        }
    }
    network.body.data.nodes.update(nodes);
}
</script>
"""

# Include the JavaScript code within the HTML file
nt.toggle_physics(False)
nt.show_buttons(filter_=['physics'])
nt.write_html('nx.html')
with open('nx.html', 'a') as file:
    file.write(js_code)


### Time complexity

In [ ]:
import time

py_times = []
c_times = []

for _ in range(100):
    init_state = np.concatenate((2*np.random.rand(N) - np.ones(N), b), axis=None)
    start_pytime = time.time()
    myProblem.rhs_type_twelve_py(0.0, init_state)
    end_of_pyQ = time.time()

    start_ctime = time.time()
    myProblem.rhs_type_twelve_c(0.0, init_state)
    end_of_cQ = time.time()
    py_time = end_of_pyQ - start_pytime
    c_time = end_of_cQ - start_ctime

    py_times.append(py_time)
    c_times.append(c_time)

print("Python time: {0}".format(sum(py_times)))
print("c time: {0}".format(sum(c_times)))

## heatmap video

In [ ]:
from pySAT import SAT, CTD, ORTANT
import numpy as np

so_file_name = 'c_libs/cSat.so'
#myProblem = SAT("SAT_problems/Benchmark_problems_N20/uf20-01.cnf", so_file_name, rhs_type=10)
myProblem = SAT("C:\\Projects\\cppSAT\\pySat\\SAT_problems\\random3SATn15a4.266666666666667.cnf", so_file_name, rhs_type=10)

N, M = myProblem.number_of_variables, myProblem.number_of_clauses
init_s = 2*np.random.rand(N) - np.ones(N)

solver = CTD(myProblem, initial_s=init_s, random_aux=False)
solver.fast_solve(t_max=5.0, solver_type='BDF', exit_type=ORTANT)

In [ ]:
generate_sym_heatmap_from_matrix(solver)

In [ ]:
plot_traj_js(solver)

In [ ]:
generate_sym_heatmap_video_from_matrices(solver)


### Pruning based on clause graph

In [ ]:
from pySAT import Warning_propagator

wp = Warning_propagator(myProblem)
clause_graph = wp.get_clause_graph()

#initial_baux = np.zeros(int(M*(M+1)/2))
#def flat_idx(i, j, M):
#    return int(i*M-i*(i+1)/2 + j)
#
#
#for m_tuple in list(clause_graph.edges()):
#    j = m_tuple[0]-N
#    i = m_tuple[1]-N
#    initial_baux[flat_idx(i, j, M)] = 1.0

initial_baux = np.zeros((M,M))

for m_tuple in list(clause_graph.edges()):
    i = m_tuple[0]-N
    j = m_tuple[1]-N
    initial_baux[i, j] = 1.0

for i in range(M):
    initial_baux[i, i] = 1.0

initial_baux= initial_baux.flatten()
init_s_2 = 2*np.random.rand(N) - np.ones(N)

In [ ]:
solver_2 = CTD(myProblem, initial_s=init_s_2, initial_baux=initial_baux)
solver_2.fast_solve(t_max=1.0, solver_type='LSODA', exit_type=ORTANT)

In [ ]:
generate_sym_heatmap_video_from_matrices(solver_2)

In [ ]:
plot_aux_js(solver_2, False)

## Pruning 3, dynamic aux

$$
\frac{ds_i}{dt} = \sum_{m,n} \left(c_{mi} K_{mi}K_m + c_{ni} K_{ni}K_n \right) \times
\begin{cases}
        b_{m n}  & \text{if } m,n \in L_{t-1},\\
      \tilde{b} & \text{otherwise.}
    \end{cases}     
$$
$$
\Delta b_{m n} = K_{m} K_{n} \times
\begin{cases}
        b_{m n}  & \text{if } m,n \in L_{t-1},\\
      \tilde{b} & \text{otherwise.}
    \end{cases}   
$$
$$
\frac{d}{dt} \tilde{b} = \frac{|| \Delta b_{m n} ||}{M}
$$
Push the largest $|| L_0 ||$ index tuple $(m,n)$ into $L_{t}$

In [ ]:
from pySAT import SAT, CTD, ORTANT, Warning_propagator
import numpy as np


so_file_name = "c_libs/cSAT.so"
so_file_name = None
myProblem = SAT("SAT_problems\\random3SATn15a4.266666666666667.cnf", so_file_name, lmbd = 0.05, rhs_type=13)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses

In [ ]:
init_s= 2*np.random.rand(N) - np.ones(N)
myProblem.number_of_auxvariables = int(M/2)
init_aux = 0.01*np.ones(myProblem.number_of_auxvariables)

In [ ]:
solver = CTD(myProblem, initial_s=init_s, initial_baux=init_aux)


In [ ]:
solver.fast_solve(t_max=550.0, solver_type='RK45', exit_type=ORTANT)

In [ ]:
plot_traj_js(solver, True)

# Egyéb

### egyéb 1

In [ ]:
from pySAT import SAT, CTD, ORTANT, HYPER_SPHERE
import numpy as np


so_file_name = 'c_libs/cSat.so'

myProblem = SAT("C:\\Projects\\cppSAT\\pySat\\SAT_problems\\random3SATn15a4.266666666666667.cnf", so_file_name, rhs_type=10)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses

init_s = 2*np.random.rand(N) - np.ones(N)

solver = CTD(myProblem, initial_s=init_s, random_aux=False)
solver.fast_solve(t_max=250, solver_type='LSODA', exit_type=ORTANT, atol=0.005, rtol=0.01)

final_b_mns = np.array([traj[-1] for traj in solver.sol.y])[N:]

generate_sym_heatmap_from_matrix(solver)




### ODE example

In [ ]:
import numpy as np
from abc import abstractclassmethod
from scipy.integrate import solve_ivp

class Problem:
    """Abstract class representing a dynamical system"""
    def __init__(self, number_of_variables):
        self.number_of_variables = number_of_variables

    @abstractclassmethod
    def rhs(self, s):
        pass

    @abstractclassmethod
    def Jakobian(self, s):
        pass

class Rössler(Problem):
    """Python class representing the 3D Rössler system"""
    def __init__(self, a = 0.398, b = 2.0, c=4) -> None:
        super().__init__(3)
        self.a = a
        self.b = b
        self.c = c

    def rhs(self, s):
        return np.array([-s[1]-s[2], s[0]+self.a*s[1], self.b+s[2]*(s[0]-self.c)])

    def Jakobian(self, s):
        return np.array([ [0.0, -1.0, -1.0], [1.0, self.a, 0.0], [s[2], 0.0, s[0]-self.c] ])

    def diff_form(self, s):
        return self.rhs(s), self.Jakobian(s)
                  
class Lorenz(Problem):
    def __init__(self, sigma=10.0, rho=28.0, beta=2.66667):
        """The "usual" parameters for the Lorenz system are the default values, for transient chaos set rho to be in the inteval [13.93,26.06]"""
        self.sigma = sigma
        self.rho = rho
        self.beta = beta
        super().__init__(3)

        def exit_hypercube(t, y) -> float:
            for coord in y[:3]:
                if coord < 1:
                    return 1.0
                print("Trajectory reached the boundary of the hypercube at t={0}".format(t))
                return -1.0
        exit_hypercube.terminal = True

        self.exit_hypercube = exit_hypercube

    def rhs(self, t, s):
        return np.array([ self.sigma*( s[1]-s[0] ), s[0]*(self.rho-s[2])-s[1], s[1]*s[0]-self.beta*s[2] ])
    
    def Jakobian(self, t, s):
        return np.array([ [-self.sigma, self.sigma, 0],[ self.rho-s[2], -1, -s[0] ], [s[1], s[0], -self.beta] ])
    
    def diff_form(self, s):
        return self.rhs(s), self.Jakobian(s)



def plot_traj(sol, number_of_variables, hide_legends = False):
    import matplotlib.pyplot as plt
    plt.grid(True)
    plt.title('State variables')
    for i, spin_var in enumerate(sol.y[0:number_of_variables]):
        x = sol.t
        y = spin_var
        plt.plot(x, y, label='s'+str(i+1))
    if not hide_legends:
        plt.legend()
    plt.show()

my_lorenz_problem = Lorenz()

solution_interval = (0.0, 50.0)
initial_state = np.array([0.5, 0.4, 0.4])

solution = solve_ivp(fun=my_lorenz_problem.rhs, 
                     t_span=solution_interval,
                     y0=initial_state,
                     method="LSODA", 
                     t_eval=None,
                     dense_output=False,
                     events=[my_lorenz_problem.exit_hypercube],
                     atol=0.001,
                     rtol=0.01,
                     jac=my_lorenz_problem.Jakobian)

plot_traj(solution, 3)



### C-LIBS testing

In [ ]:
from pySAT import SAT, CTD, ORTANT, HYPER_SPHERE
from ctypes import CDLL, POINTER, c_double, c_int, c_char
import numpy as np


so_file_name = 'c_libs/cSat.so'

myProblem = SAT("C:\\Projects\\cppSAT\\pySat\\SAT_problems\\random3SATn15a4.266666666666667.cnf", so_file_name, rhs_type=10)
#myProblem = SAT("C:\\Projects\\cppSAT\\pySat\\SAT_problems\\tiny.cnf", so_file_name, rhs_type=10)
N, M = myProblem.number_of_variables, myProblem.number_of_clauses

print(myProblem.all_solutions())


In [ ]:
import time
from pySAT import SAT, CTD, ORTANT, HYPER_SPHERE
from ctypes import CDLL, POINTER, c_double, c_int, c_char
import numpy as np

so_file_name = 'c_libs/cSat.so'

c_times = []
res = None
myProblem = None
N, M = (0, 0)
py_res = None
py_times = []

for i in range(20):
    myProblem = SAT("C:\\Projects\\cppSAT\\pySat\\SAT_problems\\random3SATn15a4.266666666666667.cnf", so_file_name, rhs_type=10)
    N, M = myProblem.number_of_variables, myProblem.number_of_clauses
   
    start = time.time()
    c_res = myProblem.all_solutions_c()
    end = time.time()
    c_times.append(end-start)
    myProblem.valid_solutions = None
    

    py_start = time.time()
    py_res = myProblem.all_solutions()
    py_end = time.time()
    py_times.append(py_end-py_start)

    myProblem.valid_solutions = None
    for sol1, sol2 in zip(c_res, py_res):
        flag = False
        for s1, s2 in zip (sol1, sol2):
            if s1 != s2:
                flag = True
                break
        if flag:
            print("oh-oh")



print("C time")
print(sum(c_times))
print('----')    
print("Python time")
print(sum(py_times))

In [ ]:
import time

bool_sol = np.array([0,1,0,1,0,0,0,1,0,0,1,0,0,1,1]).astype(np.int32)
#bool_sol = np.array([0 for i in range(N)]).astype(np.int32)


c_result = None
bool_sol_ponter = None
clauses_ponter = np.array(myProblem.clauses).ctypes.data_as(POINTER(c_int))
c_times = []
conversion_times = []
for i in range(10000):
    p1 = time.time()
    bool_sol_ponter = bool_sol.ctypes.data_as(POINTER(c_int))
    p2 = time.time()
    c_result = myProblem.cSAT_functions.check_sol(N, M, 3, bool_sol_ponter, clauses_ponter)
    end = time.time()
    c_times.append(end-p2)
    conversion_times.append(p2-p1)

print("C time")
print(sum(c_times))
print("Conversion overhead")
print(sum(conversion_times))
print("total:{0}".format(sum(c_times)+sum(conversion_times)))
print('----')

py_result = None
py_times = []
for i in range(10000):
    py_start = time.time()
    py_result = myProblem.check_solution([True if elem == 1 else False for elem in bool_sol])
    py_end = time.time()
    py_times.append((py_end - py_start))
print("Python time")
print(sum(py_times))

